In [1]:
// Functions used to read data and simulations

In [2]:
//Standard deviation of a vector
Double_t Sigma(vector<Double_t> Vector){
    int num_val = Vector.size();
    Double_t Mean=0;
    for (int i=0; i<num_val; i++){
        Mean+=Vector[i];
    }
    Mean= Mean/num_val;
    
    Double_t sigma=0;
    for (int i=0; i<num_val; i++){
        sigma+=(Vector[i]-Mean)*(Vector[i]-Mean);
    }
    sigma= sigma/(num_val-1);
    sigma = sqrt(sigma);
    return sigma;
}

In [3]:
//Smooth Step function
//--------------------------------------------------------------
double cdf(double *x, double *par){
    double mean=par[0];
    double sigma = par[1];
    
    double xx =x[0];
    return ROOT::Math::normal_cdf(xx, sigma, mean);
}

In [4]:
TH1D* Put_data_in_histo(TString filename, double real_time, TString Title){
    ifstream in;
    in.open(filename, ios::in);
    cout<<"\n*******************************************************"<<endl;
    cout<<filename<<endl;
    Float_t time=real_time/(24*3600.);
    
    Int_t x,y, MCA_chan;
    TH1D* h1 = new TH1D(Title,Title,512,-0.5,511.5);
    h1->GetXaxis()->SetTitle("Pulse Height [MCA a.u.]");
    h1->GetYaxis()->SetTitle("Counts per day per MCA channel");
    
    while (1) {
        in >> x >> y;
        if (!in.good()) break;
        
        h1->SetBinContent(x+1, y);
        h1->SetBinError(x+1, sqrt(y));
    }
    MCA_chan=h1->GetBinWidth(1);
    h1->Scale(1./(MCA_chan*time));
    return h1;
}

In [5]:
TH1D* Put_simu_in_histo_nq(TString filename, TString Title, int nBin, double Emin, double Emax, Double_t NumEv, Double_t Flux, Double_t MVthr=3.){
    TFile* Infile = new TFile(filename);
    
    Float_t ECr, EMV;
    TRandom gen(0);
    
    Double_t Plane_surf = 40.*40.; //cm2
    
    Double_t Time = NumEv/(Plane_surf*Flux); //s
    
    TTree *InTree = (TTree*) Infile->Get("NTupleAlgoDir/Pri_Ntuple");
    Int_t entries= InTree->GetEntries();
    printf(" Entries:      %10d\n",entries);
    printf(" Generated primaries:  %.0f\n",NumEv);
    printf(" Equivalent time:      %.0f s (%.3f d)\n",Time,Time/86400.);

    TH1D *histo = new TH1D(Title,Title,nBin,Emin,Emax);
    histo->GetXaxis()->SetTitle("Energy [keVee]");
    histo->GetYaxis()->SetTitle("Counts.d^{-1}.keVee^{-1}");

    InTree->SetBranchAddress("EDep", &ECr);
    InTree->SetBranchAddress("EMV0", &EMV);
    for (Int_t pk=0; pk<entries; pk++) {
        InTree->GetEntry(pk);
        
        Float_t Ep = EMV;
        
        if (Ep>0){
            Float_t sp = 0.1008*sqrt(1./Ep*(1.+1./Ep))/2.3548;      // (%)
            Ep *= (1. + sp*gen.Gaus())*1000.;
            if (Ep < MVthr*1000) continue;
        }
        
        Float_t E = ECr*1000.;                            // keV
        Float_t Enew = gen.Gaus(E, 0.084*sqrt(3500)*sqrt(E)); //Neutron peak assumed to be at 3500 keVee
        histo->Fill(Enew);
    }
    Double_t Ei = histo->GetBinWidth(1);
    histo->Scale(1./(Time/86400.)/Ei);
    
    return histo;
}

In [6]:
//This function applies a quenching factor
TH1D* Put_simu_in_histo(TString filename, TString Title, int nBin, double Emin, double Emax, Double_t NEvt, Double_t Flux =0.0134, Double_t MVthr=3., bool Veto=true, Double_t resol = 0.084){                                                      // D08 <----------
    
    TFile* Nfile = new TFile(filename);

    Float_t ECr, EMV;
    TRandom gen(0);
    
    Double_t NTime = NEvt/40./40./Flux;     // s
    
    TTree *Nnp = (TTree*) Nfile->Get("NTupleAlgoDir/Pri_Ntuple");
    TTree *Nns = (TTree*) Nfile->Get("NTupleAlgoDir/Sec_Ntuple");

    Int_t Np_entries= Nnp->GetEntries();
    Int_t Ns_entries= Nns->GetEntries();
    printf("  Primary Entries:      %10d\n",Np_entries);
    printf("  Secondary Entries:    %10d\n",Ns_entries);
    printf("  Generated primaries:  %.0f\n",NEvt);
    printf("  Equivalent time:      %.0f s (%.3f d)\n",NTime,NTime/86400.);
    
    TH1D *neut = new TH1D(Title,Title,nBin,Emin,Emax);

    neut->GetXaxis()->SetTitle("Energy [keVee]");
    neut->GetYaxis()->SetTitle("Counts.d^{-1}.keVee^{-1}");

    Nnp->SetBranchAddress("EDep", &ECr);
    if (Veto){Nnp->SetBranchAddress("EMV0", &EMV);}

    Float_t NpNSec,NpDelay, NsPDG,NsPidM,NsPid;
    Nnp->SetBranchAddress(  "NSec", &NpNSec);
    Nnp->SetBranchAddress( "Delay", &NpDelay);
    Nns->SetBranchAddress(   "PDG", &NsPDG);
    Nns->SetBranchAddress(  "PidM", &NsPidM);
    Nns->SetBranchAddress(   "Pid", &NsPid);
    
    // Calculate a constant q.f. from the position, on the gamma calibrated Energy scale, of the thermal neutron peak (expected at 4.78 MeVee)
    Float_t qf = 3500/4780.; //Quenching factor Emin + 326/512(Position of neutron peak/number of bins)*(Emax-Emin)/4780(Qvalue the neutron capture)
    
    // Loop on primary particles pk
    Int_t pk=0, sk=0, npCheck=0, nsCheck=0, isQF=0, nQuenched=0;
    
    while (pk < Np_entries) {
        
        // Loop on secondary particles sk (defined as those particles entering in the LiI(Eu) crystal)
        if (sk < Ns_entries) Nns->GetEntry(sk);
        
        // Get the "id" of the primary particles associated to the secondary particle sk
        Int_t id = ((Int_t) (NsPidM+0.5))*1000000 + ((Int_t) (NsPid+0.5));
        
         // if the primary particles is pk (the one under examination in primary loop), set isQF=1 in the cases when the
        // secondary particle sk is a neutron or antineutron
        // ==> i.e., if the secondary particles entering in the LiI(Eu) crystal is a neutron, the deposited energy is due
        // to a neutron interaction in LiI(Eu) detector and the quenching factor has to be applied (isQF=1, --> true).
        if(id==pk && sk < Ns_entries) {
            if (NsPDG==2112 || NsPDG==-2112) isQF=1;
            sk++;
            nsCheck++;
        } 
        
        // otherwise, no further secondary particles are associated to pk, I can fill the spectrum with the deposited
        // energy in LiI(Eu) detector (branch EDep in primary ntuple), applying or not the quenching factor
        else {
            Nnp->GetEntry(pk);
            // it is only a consinstency check (verify that the number of analysed secondary particles is the expected one)
            // for the pk primary particle under examination
            if (NpNSec != nsCheck) printf(" Primary entry %d: NSec error NSec=%d, nsCheck=%d\n", pk, (int) NpNSec, nsCheck);
    
            // It happens sometime that the primary particles is not associated to any secondary particles (NpNSec=0);
            // Almost always, it is due to very slow neutrons that after entering the LiI(Eu) crystal need long time before
            // having an interaction, and therefore are classified as new, delayed events (NpDelay>0) and loose their correlation
            // with the secondary particle ntuple. Also these events have to be classified as neutron events ==> isQF=1
            // (this point is not easy to explain, maybe we can have a short discussion about it)
            if (NpNSec==0 && NpDelay>0) isQF=1;        // Sicuramente neutroni
            if (isQF == 1) nQuenched++;
            
            // the E deposition in the MV is spread accounting for energy resolution resolution
            Float_t Ep = EMV;
        
            if (Ep>0){
                Float_t sp = 0.1008*sqrt(1./Ep*(1.+1./Ep))/2.3548;      // (%)
                Ep *= (1. + sp*gen.Gaus())*1000.;
            }
            
            if (Veto){
                if (Ep < MVthr*1000) {
                    Float_t E = ECr*1000.;                                  // keV

                    if (isQF==1) E *= qf;
                    Double_t Enew = gen.Gaus(E, resol*sqrt(3500)*sqrt(E)); //Neutron peak assumed to be at 3500 keVee                           // keV
                    neut->Fill(Enew);
                } // else printf("Ep = %f keV\n",EMV);
            }
            
            else {
                Float_t E = ECr*1000.;                                  // keV

                if (isQF==1) E *= qf;
                Double_t Enew = gen.Gaus(E, resol*sqrt(3500)*sqrt(E)); //Neutron peak assumed to be at 3500 keVee                           // keV
                neut->Fill(Enew);
            }
            
            npCheck++;
            nsCheck=0;
            isQF=0;
            pk++;
        }
    }

    printf(" Nb of primary analysed: %d\n", npCheck);
    printf(" Nb of events quenched : %d\n", nQuenched);
    
    Double_t Ei = neut->GetBinWidth(1);
    neut->Scale(1./(NTime/86400.)/Ei);
    return neut;
}

In [7]:
// Residual histogram
TH1D* Residuals(TH1D* histo_data, TF1* Model, Double_t Min, Double_t Max, bool pc = true){
    TH1D* hRes = (TH1D*) histo_data->Clone();
    double Value_i, E_i, Diff_i, Error_i;
    double chi2=0;
    for (int i = 1; i<hRes->GetNbinsX(); i++){
        Value_i = hRes->GetBinContent(i);
        E_i = hRes->GetBinCenter(i);
        if (Value_i>0&&E_i>Min&&E_i<Max) {
            Diff_i = histo_data->GetBinContent(i)-Model->Eval(E_i);
            Error_i = histo_data->GetBinError(i);
            if (pc) {
                hRes->SetBinContent(i, Diff_i/Value_i*100);
                hRes->SetBinError(i, Error_i/Value_i*100);
            }
            else {
                hRes->SetBinContent(i, Diff_i/Error_i);
                hRes->SetBinError(i, 1);
            }
            chi2+=(Diff_i*Diff_i)/(Error_i*Error_i);
        }
        else hRes->SetBinContent(i, 0);
    }

    //cout<<"\nChi2/ndf = "<<chi2<<"/"<<Model->GetNDF()<<" = "<<chi2/Model->GetNDF()<<endl;
    hRes->SetLineColor(Model->GetLineColor());
    hRes->SetTitle("");
    if (pc) hRes->GetYaxis()->SetRangeUser(-100, 100);
    else hRes->GetYaxis()->SetRangeUser(-20, 20);
    return hRes;
}

In [8]:
// Residual histogram
std::vector<TH1D*> Residuals_vec(TH1D* histo_data, TF1* Model, Double_t Min, Double_t Max, bool pc = true){
    TH1D* hRes = (TH1D*) histo_data->Clone();
    TString Title = histo_data->GetTitle();
    TH1D* hReducedRes = new TH1D("Reduced_res_"+Title,"Reduced_res_"+Title, 50, -10, 10);
    
    double Value_i, E_i, Diff_i, Error_i;
    double chi2=0;
    for (int i = 1; i<hRes->GetNbinsX(); i++){
        Value_i = hRes->GetBinContent(i);
        E_i = hRes->GetBinCenter(i);
        if (Value_i>0&&E_i>Min&&E_i<Max) {
            Diff_i = histo_data->GetBinContent(i)-Model->Eval(E_i);
            Error_i = histo_data->GetBinError(i);
            hReducedRes->Fill(Diff_i/Error_i);
            if (pc) {
                hRes->SetBinContent(i, Diff_i/Value_i*100);
                hRes->SetBinError(i, Error_i/Value_i*100);
            }
            else {
                hRes->SetBinContent(i, Diff_i/Error_i);
                hRes->SetBinError(i, 1);
            }
            chi2+=(Diff_i*Diff_i)/(Error_i*Error_i);
        }
        else {
            hRes->SetBinContent(i, 0);
            hRes->SetBinError(i, 0);
        }
    }

    //cout<<"\nChi2/ndf = "<<chi2<<"/"<<Model->GetNDF()<<" = "<<chi2/Model->GetNDF()<<endl;
    hRes->SetLineColor(Model->GetLineColor());
    hRes->SetTitle("");
    
    hReducedRes->SetFillColor(Model->GetLineColor());
    hReducedRes->SetLineColor(Model->GetLineColor());
    hReducedRes->SetTitle("");
    
    if (pc) hRes->GetYaxis()->SetRangeUser(-100, 100);
    else hRes->GetYaxis()->SetRangeUser(-20, 20);
    hReducedRes->GetXaxis()->SetRangeUser(-5, 5);
    
    std::vector<TH1D*> histos;
    histos.push_back(hRes);
    histos.push_back(hReducedRes);
    return histos;
}

In [9]:
%jsroot on
#include <TFitResult.h>

# Analysis of the 9 inches sphere

Load the runs taken in the different locations with the 9inch sphere and the LII(Eu) detector. Those in the VNS, and the Double Chooz Hut (DC Hut) are taken with a muon veto panel in anti-coincidences.

## Data

### CryoLab

In [10]:
TH1D* h_CryoLab_9inch = Put_data_in_histo("Measures@TUM/02-21_BkgSpektrum_CryoLab_BS-EXT_72h.dat", 72*3600, "BS-EXT at Cryolab atm neutrons");
h_CryoLab_9inch->Rebin(4);
h_CryoLab_9inch->Scale(1/4.);


*******************************************************
Measures@TUM/02-21_BkgSpektrum_CryoLab_BS-EXT_72h.dat


In [11]:
TH1D* h_CryoLab_9inch_MV = Put_data_in_histo("Measures@TUM/03-28_BkgSpektrum_CryoLab_BS-EXT_19h.dat", 19*3600, "BS-EXT at Cryolab atm neutrons with MV");
h_CryoLab_9inch_MV->Rebin(4);
h_CryoLab_9inch_MV->Scale(1/4.);


*******************************************************
Measures@TUM/03-28_BkgSpektrum_CryoLab_BS-EXT_19h.dat


In [12]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();

h_CryoLab_9inch->SetLineColor(kRed);
h_CryoLab_9inch->Draw("");
h_CryoLab_9inch_MV->SetLineColor(kBlue);
h_CryoLab_9inch_MV->Draw("Same");
gStyle->SetOptStat(0);
TLegend* leg = new TLegend(0.8, 0.8);
leg->AddEntry(h_CryoLab_9inch, "NoMV");
leg->AddEntry(h_CryoLab_9inch_MV, "MV");
leg->Draw("same");

Double_t Error, Error_MV;

cout<<"Number of events in the Neutron peak = "<<h_CryoLab_9inch->IntegralAndError(h_CryoLab_9inch->FindBin(258), h_CryoLab_9inch->FindBin(388), Error, "width")<<" +- "<<Error<< endl;
cout<<"Number of events in the Neutron peak = "<< h_CryoLab_9inch_MV->IntegralAndError(h_CryoLab_9inch_MV->FindBin(200), h_CryoLab_9inch_MV->FindBin(340), Error_MV, "width")<<" +- "<<Error_MV<<endl;

Number of events in the Neutron peak = 292.333 +- 9.8714
Number of events in the Neutron peak = 248.842 +- 17.7293


### CrystalLab

In [13]:
TH1D* h_Crystal_9inch = Put_data_in_histo("Measures@TUM/03-03_BkgSpektrum_CrystalLab_BS-EXT_141h.dat", 141*3600, "9inch at CrystalLab atm neutrons");
h_Crystal_9inch->Rebin(4);
h_Crystal_9inch->Scale(1/4.);


*******************************************************
Measures@TUM/03-03_BkgSpektrum_CrystalLab_BS-EXT_141h.dat


### VNS 

In [14]:
TH1D* h_VNS_9inch_1 = Put_data_in_histo("Measures@VNS/2022-04-27_BS-EXT_RT_1122274.88_LV_1121904.17.dat", 1122274., "9inch at VNS - 1");
h_VNS_9inch_1->Rebin(4);
h_VNS_9inch_1->Scale(1/4.);

TH1D* h_VNS_9inch_2 = Put_data_in_histo("Measures@VNS/2022-06-07_BS-EXT_RT_1140078.50_LV_1139756.64.dat", 1140078, "9inch at VNS - 2");
h_VNS_9inch_2->Rebin(4);
h_VNS_9inch_2->Scale(1/4.);

TH1D* h_VNS_9inch_3 = Put_data_in_histo("Measures@VNS/2022-07-19_BS-EXT_RT_2242568.15_LV_2241965.42.dat", 2242568, "9inch at VNS - 3");
h_VNS_9inch_3->Rebin(4);
h_VNS_9inch_3->Scale(1/4.);


*******************************************************
Measures@VNS/2022-04-27_BS-EXT_RT_1122274.88_LV_1121904.17.dat

*******************************************************
Measures@VNS/2022-06-07_BS-EXT_RT_1140078.50_LV_1139756.64.dat

*******************************************************
Measures@VNS/2022-07-19_BS-EXT_RT_2242568.15_LV_2241965.42.dat


In [15]:
TH1D* h_VNS_9inch_sum = (TH1D*) h_VNS_9inch_1->Clone();
h_VNS_9inch_sum->Add(h_VNS_9inch_sum, h_VNS_9inch_2, 1/3., 1/3.); 
h_VNS_9inch_sum->Add(h_VNS_9inch_sum, h_VNS_9inch_3, 1, 1/3.);
h_VNS_9inch_sum->SetTitle("9inch at VNS - sum");

The 3 runs taken in the VNS are sumed, without any shift or recalibration, we are considering that the gain didn't change during the whole period of data taking. Here the 3 spectra and the sum are superimposed to check the stability of the measurements.

In [16]:
TCanvas* C3 = new TCanvas();
C3->Draw();
C3->SetLogy();
//h_CryoLab_8inch->GetYaxis()->SetRangeUser(0, 500);
h_VNS_9inch_1->SetLineColor(kRed);
h_VNS_9inch_1->Draw("");
h_VNS_9inch_2->SetLineColor(kBlue);
h_VNS_9inch_2->Draw("Same");
h_VNS_9inch_3->SetLineColor(kGreen);
h_VNS_9inch_3->Draw("Same");
h_VNS_9inch_sum->SetLineColor(kBlack);
h_VNS_9inch_sum->Draw("SAME");
gStyle->SetOptStat(0);
TLegend* leg = new TLegend(0.8, 0.8);
leg->AddEntry(h_VNS_9inch_1, "1");
leg->AddEntry(h_VNS_9inch_2, "2");
leg->AddEntry(h_VNS_9inch_3, "3");
leg->AddEntry(h_VNS_9inch_sum, "sum");
leg->Draw("same");

### DCHut

The two runs taken in the DCHut are sumed. No shift, no calibration.

In [17]:
TH1D* h_DC_9inch_1 = Put_data_in_histo("Measures@DCHut/2022-08-25_BS-EXT_RT_1282905.28_LV_1282579.20.dat", 1282579., "9inch at DChut - 1");
h_DC_9inch_1->Rebin(4);
h_DC_9inch_1->Scale(1/4.);

TH1D* h_DC_9inch_2 = Put_data_in_histo("Measures@DCHut/2022-10-04_BS-EXT_RT_1748999.66_LV_1748473.16.dat", 1748473., "9inch at DChut - 2");
h_DC_9inch_2->Rebin(4);
h_DC_9inch_2->Scale(1/4.);


*******************************************************
Measures@DCHut/2022-08-25_BS-EXT_RT_1282905.28_LV_1282579.20.dat

*******************************************************
Measures@DCHut/2022-10-04_BS-EXT_RT_1748999.66_LV_1748473.16.dat


In [18]:
TH1D* h_DC_9inch_sum = (TH1D*) h_DC_9inch_1->Clone();
h_DC_9inch_sum->Add(h_DC_9inch_sum, h_DC_9inch_2, 1/2., 1/2.); 
h_DC_9inch_sum->SetTitle("9inch at DCHut - sum");

In [19]:
TCanvas* C4 = new TCanvas();
C4->Draw();
C4->SetLogy();
h_DC_9inch_1->Draw();
h_DC_9inch_2->SetLineColor(kRed);
h_DC_9inch_2->Draw("SAME");
h_DC_9inch_sum->SetLineColor(kBlack);
h_DC_9inch_sum->Draw("SAME");

gStyle->SetOptStat(0);
TLegend* leg = new TLegend(0.9, 0.9);
leg->AddEntry(h_DC_9inch_1, "1");
leg->AddEntry(h_DC_9inch_2, "2");
leg->AddEntry(h_DC_9inch_sum, "sum");
leg->Draw("same");

### Calibration

In [20]:
TH1D* h_Cal_9inch = Put_data_in_histo("Measures@TUM/03-14_Cf252_LMU_BS-EXT_3h.dat", 3*24*3600., "9inch with Cf252 n source");
h_Cal_9inch->Rebin(4);
h_Cal_9inch->Scale(1/4.);


*******************************************************
Measures@TUM/03-14_Cf252_LMU_BS-EXT_3h.dat


## Calibration of data spectra

### Peak position from neutron calibration run with Cf

In order to calibrate the data, the peak position from the source run performed at TUM is fittted to obtain a calibration factor.

In [21]:
TF1* Neutron_peak_Gaus_MCA = new TF1("Neutron_peak_MCA", "[0]*TMath::Gaus(x, [1], [2])", 200, 500); //Gaussian function to fit the neutron calibration run
Neutron_peak_Gaus_MCA->SetParNames("Amplitude [Counts/MCA]", "#mu [MCA]", "#sigma [MCA]");
Neutron_peak_Gaus_MCA->SetParameters(10, 350, 40);
h_Cal_9inch->Fit("Neutron_peak_MCA", "R");

Double_t Cal_factor = 3500./Neutron_peak_Gaus_MCA->GetParameter(1); //Neutron peak assumed to be at 3500keVee
Double_t err_Cal_factor = (Neutron_peak_Gaus_MCA->GetParError(1))/(Neutron_peak_Gaus_MCA->GetParameter(1))*Cal_factor; //Neutron peak assumed to be at 3500keVee
Double_t Resol_NP = Neutron_peak_Gaus_MCA->GetParameter(2)/Neutron_peak_Gaus_MCA->GetParameter(1);

 FCN=81.5498 FROM MIGRAD    STATUS=CONVERGED     115 CALLS         116 TOTAL
                     EDM=1.2986e-11    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Amplitude [Counts/MCA]   6.75390e+00   2.30968e-01   8.23300e-04   5.54859e-06
   2  #mu [MCA]    3.26923e+02   7.21874e-01   3.18575e-03  -3.52185e-06
   3  #sigma [MCA]   2.60852e+01   5.32647e-01   1.89244e-03   9.01873e-06


In [22]:
TCanvas* C8 = new TCanvas();
C8->Draw();
C8->SetLogy();
h_Cal_9inch->Draw();

In [23]:
cout<<"The calibration factor is equal to "<<Cal_factor<<" keVee/MCA"<<endl;

The calibration factor is equal to 10.7059 keVee/MCA


### Apply to data spectra 

This calibration is applied to the data spectra.

In [24]:
TH1D* Calibrate_histo(TH1D* histo, Double_t CalibVal, TString NewTitle){
    Int_t NBins = histo->GetNbinsX();
    Int_t MCA_min = histo->GetBinCenter(1);
    Int_t MCA_max = histo->GetBinCenter(NBins);
    
    TH1D* Calib_histo = new TH1D(NewTitle, Form("%s_keVee", histo->GetTitle()), NBins, MCA_min*CalibVal, MCA_max*CalibVal);
    Int_t MCA_i;
    Double_t E_cal, MCA_i_content, MCA_i_Error;
    for(int i=0; i<NBins; i++){
        MCA_i = histo->GetBinCenter(i);
        MCA_i_content = histo->GetBinContent(i)*histo->GetBinWidth(i);
        MCA_i_Error = histo->GetBinError(i)*histo->GetBinWidth(i);
        E_cal = MCA_i*CalibVal;
        int Bin_Ecal = Calib_histo->FindBin(E_cal);
        Double_t prev_val_Ecal = Calib_histo->GetBinContent(Bin_Ecal);
        Double_t prev_err_Ecal = Calib_histo->GetBinError(Bin_Ecal);
        Calib_histo->SetBinContent(Bin_Ecal, prev_val_Ecal+MCA_i_content/Calib_histo->GetBinWidth(i));
        Calib_histo->SetBinError(Bin_Ecal, sqrt(prev_err_Ecal*prev_err_Ecal+(MCA_i_Error/Calib_histo->GetBinWidth(i))*(MCA_i_Error/Calib_histo->GetBinWidth(i))));
    }
    Calib_histo->GetXaxis()->SetTitle("Calibrated Energy [keVee]");
    Calib_histo->GetYaxis()->SetTitle("Differential rate (ev.d^{-1}.keVee^{-1})");

    return Calib_histo;
}

In [25]:
//Cryolab
TH1D* hCal_CryoLab_9inch = Calibrate_histo(h_CryoLab_9inch, Cal_factor, Form("%s_keVee", h_CryoLab_9inch->GetTitle()));
TH1D* hCal_CryoLab_9inch_MV = Calibrate_histo(h_CryoLab_9inch_MV, Cal_factor*3550/3000., Form("%s_keVee", h_CryoLab_9inch_MV->GetTitle()));

In [26]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();

hCal_CryoLab_9inch->SetLineColor(kRed);
hCal_CryoLab_9inch->SetTitle("");
hCal_CryoLab_9inch->Draw("");
hCal_CryoLab_9inch_MV->SetLineColor(kBlue);
hCal_CryoLab_9inch_MV->Draw("Same");
gStyle->SetOptStat(0);

TLegend* leg = new TLegend(0.8, 0.8);
leg->AddEntry(hCal_CryoLab_9inch, "No MV");
leg->AddEntry(hCal_CryoLab_9inch_MV, "with MV");
leg->SetLineColor(kWhite);
leg->Draw("same");

In [27]:
//Crystal Lab
TH1D* hCal_Crystal_9inch = Calibrate_histo(h_Crystal_9inch, Cal_factor, Form("%s_keVee", h_Crystal_9inch->GetTitle()));

In [28]:
//VNS
TH1D* hCal_VNS_9inch = Calibrate_histo(h_VNS_9inch_sum, Cal_factor, Form("%s_keVee", h_VNS_9inch_sum->GetTitle()));

In [29]:
//DCHut
TH1D* hCal_DC_9inch = Calibrate_histo(h_DC_9inch_sum, Cal_factor, Form("%s_keVee", h_DC_9inch_sum->GetTitle()));

## Simulation results

Load the simulations of ambient gammas, atmospheric muons and neutrons with the 9inch sphere, performed by Fabio. Analyzed with the Ntuple algo. The corresponding histograms are calculated from Fabio's method in BS_BkgModel.C : the Muon veto panel is taken into account with a 3 MeV cut. The quenching factor for neutron energy deposition is calculated in order to have a neutron capture peak at 3.5 MeVee. An arbitrary resolution is applied bu will not be considered for the fitting procedure.

### Gammas

In [30]:
int nbins = hCal_DC_9inch->GetNbinsX();
double hEmin = hCal_DC_9inch->GetBinLowEdge(1);
double hEmax = hCal_DC_9inch->GetBinLowEdge(nbins)+hCal_DC_9inch->GetBinWidth(nbins);
TH1D* h_SimuGamma_9inch = Put_simu_in_histo("Simulations/Env_Gammas/BS_D09/Analyzer_T_run01-09.root", "9 inches environmental gammas", nbins, hEmin, hEmax, 1.20e10, 3.3, 3., false, 0.084);

  Primary Entries:          158126
  Secondary Entries:        163150
  Generated primaries:  12000000000
  Equivalent time:      2272727 s (26.305 d)
 Nb of primary analysed: 158126
 Nb of events quenched : 0


### Muons

With secondary neutrons quenched

In [31]:
TH1D* h_SimuMuons_9inch = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (with MV 6. MeV thr)", nbins, hEmin, hEmax, 5.6e7, 0.019, 6., true, 0.084);

  Primary Entries:          400797
  Secondary Entries:        468366
  Generated primaries:  56000000
  Equivalent time:      1842105 s (21.321 d)
 Nb of primary analysed: 400797
 Nb of events quenched : 1124


In [32]:
TH1D* h_SimuMuons_9inch_1MeV = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (with MV 1 MeV thr)", nbins, hEmin, hEmax, 7.20e8, 0.019, 1., true);
h_SimuMuons_9inch_1MeV->Fit("landau", "R0", "", 1100, 2300);

TH1D* h_SimuMuons_9inch_5MeV = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (with MV 5 MeV thr)", nbins, hEmin, hEmax, 7.20e8, 0.019, 5., true);

TH1D* h_SimuMuons_9inch_7MeV = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (with MV 7 MeV thr)", nbins, hEmin, hEmax, 7.20e8, 0.019, 7., true);
h_SimuMuons_9inch_7MeV->Fit("landau", "R0", "", 800, 2000);

TH1D* h_SimuMuons_9inch_noMV = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (without MV)", nbins, hEmin, hEmax, 7.20e8, 0.019, 10., false);
h_SimuMuons_9inch_noMV->Fit("landau", "R0", "", 800, 1900);

TH1D* h_SimuMuons_9inch45deg_noMV = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_BS9_45deg.root", "9 inches tilt 45deg - atmospheric muons (without MV)", nbins, hEmin, hEmax, 5.0e8, 0.019, 10., false);
h_SimuMuons_9inch45deg_noMV->Fit("landau", "R0", "", 800, 1900);

TCanvas *C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_9inch_1MeV->GetYaxis()->SetRangeUser(1e-3, 10);
h_SimuMuons_9inch_1MeV->SetLineColor(kBlue);
h_SimuMuons_9inch_5MeV->SetLineColor(kRed);
h_SimuMuons_9inch_7MeV->SetLineColor(kMagenta);
h_SimuMuons_9inch_noMV->SetLineColor(kBlack);
h_SimuMuons_9inch45deg_noMV->SetLineColor(kGreen);
h_SimuMuons_9inch_1MeV->Draw("HIST");
h_SimuMuons_9inch_5MeV->Draw("HIST SAME");
h_SimuMuons_9inch_7MeV->Draw("HIST SAME");
h_SimuMuons_9inch_noMV->Draw("HIST SAME");
h_SimuMuons_9inch45deg_noMV->Draw("HIST SAME");


h_SimuMuons_9inch_1MeV->SetTitle("");
TLegend* leg0 = new TLegend(0.6, 0.7, 0.89, 0.89);
leg0->AddEntry(h_SimuMuons_9inch_1MeV, "MV thr 1MeV");
leg0->AddEntry(h_SimuMuons_9inch_5MeV, "MV thr 5MeV");
leg0->AddEntry(h_SimuMuons_9inch_7MeV, "MV thr 7MeV");
leg0->AddEntry(h_SimuMuons_9inch_noMV, "no MV");
leg0->AddEntry(h_SimuMuons_9inch45deg_noMV, "tilt 45deg - no MV");
leg0->Draw("SAME");
leg0->SetLineWidth(0);

  Primary Entries:          400797
  Secondary Entries:        468366
  Generated primaries:  720000000
  Equivalent time:      23684211 s (274.123 d)
 Nb of primary analysed: 400797
 Nb of events quenched : 1124
 FCN=38.8669 FROM MIGRAD    STATUS=CONVERGED     120 CALLS         121 TOTAL
                     EDM=2.40965e-09    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant     1.13466e+00   7.69134e-03   1.58618e-05   6.65119e-03
   2  MPV          1.43386e+03   4.04968e+00   1.14933e-02  -1.02651e-05
   3  Sigma        2.53622e+02   3.40091e+00   8.02308e-06   1.42441e-02
  Primary Entries:          400797
  Secondary Entries:        468366
  Generated primaries:  720000000
  Equivalent time:      23684211 s (274.123 d)
 Nb of primary analysed: 400797
 Nb of events quenched : 1124
  Primary Entries:          400797
  Secondary Entries

In [33]:
TH1D* h_SimuMuons_9inch_0_07 = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (no MV, resolution 0.07)", nbins, hEmin, hEmax, 7.20e8, 0.019, 1., false, 0.07);

TH1D* h_SimuMuons_9inch_0_09 = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (no MV, resolution 0.09)", nbins, hEmin, hEmax, 7.20e8, 0.019, 1., false, 0.09);

TH1D* h_SimuMuons_9inch_0_1 = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (no MV, resolution 0.1)", nbins, hEmin, hEmax, 7.20e8, 0.019, 1., false, 0.1);

TH1D* h_SimuMuons_9inch_0_2 = Put_simu_in_histo("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (no MV, resolution 0.2)", nbins, hEmin, hEmax, 7.20e8, 0.019, 1., false, 0.2);

TCanvas *C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_9inch_0_07->GetYaxis()->SetRangeUser(1e-3, 10);
h_SimuMuons_9inch_0_07->SetLineColor(kBlue);
h_SimuMuons_9inch_0_09->SetLineColor(kRed);
h_SimuMuons_9inch_0_1->SetLineColor(kMagenta);
h_SimuMuons_9inch_0_2->SetLineColor(kBlack);
h_SimuMuons_9inch_0_1->Draw("HIST");
h_SimuMuons_9inch_0_09->Draw("HIST SAME");
h_SimuMuons_9inch_0_1->Draw("HIST SAME");
h_SimuMuons_9inch_0_2->Draw("HIST SAME");
h_SimuMuons_9inch->Draw("HIST SAME");

  Primary Entries:          400797
  Secondary Entries:        468366
  Generated primaries:  720000000
  Equivalent time:      23684211 s (274.123 d)
 Nb of primary analysed: 400797
 Nb of events quenched : 1124
  Primary Entries:          400797
  Secondary Entries:        468366
  Generated primaries:  720000000
  Equivalent time:      23684211 s (274.123 d)
 Nb of primary analysed: 400797
 Nb of events quenched : 1124
  Primary Entries:          400797
  Secondary Entries:        468366
  Generated primaries:  720000000
  Equivalent time:      23684211 s (274.123 d)
 Nb of primary analysed: 400797
 Nb of events quenched : 1124
  Primary Entries:          400797
  Secondary Entries:        468366
  Generated primaries:  720000000
  Equivalent time:      23684211 s (274.123 d)
 Nb of primary analysed: 400797
 Nb of events quenched : 1124


Without quenching

In [34]:
TH1D* h_SimuMuons_9inch_nq = Put_simu_in_histo_nq("Simulations/Atm_Muons/BS_D09/Analyzer_T_run01-09.root", "9 inches - atmospheric muons (with MV 6 MeV thr)", nbins, hEmin, hEmax, 7.20e8, 0.019, 6.);

 Entries:          400797
 Generated primaries:  720000000
 Equivalent time:      23684211 s (274.123 d)


### Atmospheric neutrons 

With quenching

In [35]:
TH1D* h_SimuNeutrons_9inch = Put_simu_in_histo("Simulations/Atm_Neutr/BS_D09/Analyzer_T_run01-15.root", "9 inches - atmospheric neutrons (with MV)", nbins, hEmin, hEmax, 1.50e9, 0.0134, 6.);

  Primary Entries:          385573
  Secondary Entries:         87314
  Generated primaries:  1500000000
  Equivalent time:      69962687 s (809.753 d)
 Nb of primary analysed: 385573
 Nb of events quenched : 353346


Without quenching

In [36]:
TH1D* h_SimuNeutrons_9inch_nq = Put_simu_in_histo_nq("Simulations/Atm_Neutr/BS_D09/Analyzer_T_run01-15.root", "9 inches - atmospheric neutrons (with MV)", nbins, hEmin, hEmax, 1.50e9, 0.0134, 6.);

 Entries:          385573
 Generated primaries:  1500000000
 Equivalent time:      69962687 s (809.753 d)


Here the simulation muon (blue) and neutron (black) whitout quenching are plotted. the bump at high energy it the muon queue is assumed to be secondary neutrons from spallation in the lead. For the next part of the analysis, those two simulations are analyzed by quenching the neutrons. </br>
<b> To be checked </b> How exactly the neutrons are identified to be quenched? Is it possible to have process in which the neutrons can deposit a non quenched energy? 

In [37]:
TCanvas *C = new TCanvas();
C->Draw();
h_SimuMuons_9inch_nq->Draw();
h_SimuNeutrons_9inch_nq->SetLineColor(kBlack);
h_SimuNeutrons_9inch_nq->Draw("SAME");

## Background models

Use the simulations to constrain the shape of the background model which will be used to fit the measurements.

### Gamma Background 

The gamma background is fitted with the sum of two exponentials linked by a smooth step function. 

1- First exponential fitted between 1200 and 5000 keVee

In [38]:
TF1* Gamma_background_1 = new TF1("Gamma_background_1", "expo", 1000, 5000); 
Gamma_background_1->SetParNames("Constant []", "Slope [keVee^{-1}]");
Gamma_background_1->SetParameter(0,1);
Gamma_background_1->SetParameter(1,100);
h_SimuGamma_9inch->Fit("Gamma_background_1", "R", "", 1100, 2800); //Decreasing exponentialin the ROI [1.2; 2.8] MeVee

Gamma_background_1->FixParameter(0, Gamma_background_1->GetParameter(0));
Gamma_background_1->FixParameter(1, Gamma_background_1->GetParameter(1));

 FCN=40.8949 FROM MIGRAD    STATUS=CONVERGED      57 CALLS          58 TOTAL
                     EDM=3.0396e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant []   2.84951e+00   7.57442e-02   5.01019e-05  -1.46439e-02
   2  Slope [keVee^{-1}]  -3.20014e-03   5.21478e-05   3.44944e-08  -1.92077e+01


2- Second exponential fitted between 200 and 1000 keVee

In [39]:
TF1* Gamma_background_2 = new TF1("Gamma_background_2", "expo", 100, 1000); 
Gamma_background_2->SetParNames("Constant []", "Slope [keVee^{-1}]");
Gamma_background_2->SetParameter(0,1);
Gamma_background_2->SetParameter(1,100);
h_SimuGamma_9inch->Fit("Gamma_background_2", "R", "", 300, 1100); 

Gamma_background_2->FixParameter(0, Gamma_background_2->GetParameter(0));
Gamma_background_2->FixParameter(1, Gamma_background_2->GetParameter(1));

 FCN=132.435 FROM MIGRAD    STATUS=CONVERGED      51 CALLS          52 TOTAL
                     EDM=1.80058e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant []   2.38989e+00   1.65475e-02   3.00885e-05   3.32466e-02
   2  Slope [keVee^{-1}]  -2.97123e-03   2.77471e-05   5.04512e-08   1.63367e+01


The global function for the gamma background model is a sum of those two exponentials, linked by a smooth step function (cdf) with two parameters: its position and its width.

In [40]:
Double_t Gammas(Double_t* x, Double_t *par){
    Double_t par_cdf[2]= {par[2], par[3]};
    return (1-cdf(x, par_cdf))*par[0]*Gamma_background_2->Eval(x[0])+cdf(x, par_cdf)*par[1]*Gamma_background_1->Eval(x[0]);
}

In [41]:
TF1* Gamma_shape_9inch = new TF1("Gamma_shape_9inch", Gammas, 300, 5000, 4);
Gamma_shape_9inch->SetParNames("Norm_expo1", "Norm_expo2", "pos cdf", "sigma cdf");
Gamma_shape_9inch->SetParameter(2, 500);
Gamma_shape_9inch->SetParameter(3, 200);
Gamma_shape_9inch->SetParLimits(3, 10, 1000);
h_SimuGamma_9inch->Fit("Gamma_shape_9inch", "R");

 FCN=141.738 FROM MIGRAD    STATUS=CONVERGED     597 CALLS         598 TOTAL
                     EDM=6.45784e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_expo1   9.90022e-01   5.78766e-03   3.20539e-05   3.71163e-02
   2  Norm_expo2   1.00729e+00   2.05961e-02   8.76466e-05   1.80514e-02
   3  pos cdf      1.03575e+03   3.46328e+01   1.24074e-01  -5.73777e-06
   4  sigma cdf    1.20913e+02   3.06842e+01   4.06346e-04  -1.69924e-03


In [42]:
TCanvas* C10 = new TCanvas();
C10->Draw();
C10->SetLogy();
h_SimuGamma_9inch->Draw("");

### Muon background

The muon background model is made of three components: a Landau for the peak, a pol2 for the plateau region and another Landau for the queue at high energies.

1- Muon Peak with a landau

In [43]:
TF1* Muon_peak_9inch = new TF1("Muon_peak_9inch", "landau", 1200, 2200); //Landau in muon peak region
Muon_peak_9inch->SetParNames("Amplitude_mu []", "MPV [keVee]", "[Sigma [keVee]]");
Muon_peak_9inch->SetParameters(1,1100,100);
h_SimuMuons_9inch->Fit("Muon_peak_9inch", "R");

Muon_peak_9inch->FixParameter(0,Muon_peak_9inch->GetParameter(0));
Muon_peak_9inch->FixParameter(1,Muon_peak_9inch->GetParameter(1));
Muon_peak_9inch->FixParameter(2,Muon_peak_9inch->GetParameter(2));

 FCN=9.12923 FROM MIGRAD    STATUS=CONVERGED     131 CALLS         132 TOTAL
                     EDM=6.70318e-11    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Amplitude_mu []   2.00686e+01   1.33515e-01   1.33654e-04  -7.72793e-05
   2  MPV [keVee]   1.37005e+03   7.55989e+00   5.76676e-03  -2.71145e-06
   3  [Sigma [keVee]]   2.28563e+02   3.53404e+00   3.73211e-06  -4.67748e-03


In [44]:
TCanvas* C11 = new TCanvas();
C11->Draw();
C11->SetLogy();
h_SimuMuons_9inch->SetLineColor(kBlack);
h_SimuMuons_9inch->Draw("");

2- Muon Plateau with a pol2 between 400 and 1200 keVee

In [45]:
TF1* Muon_plateau_9inch = new TF1("Muon_plateau_9inch", "pol2", 200, 900); 
Muon_plateau_9inch->SetParNames("a", "b", "c");
h_SimuMuons_9inch->Fit("Muon_plateau_9inch", "R");

Muon_plateau_9inch->FixParameter(0,Muon_plateau_9inch->GetParameter(0));
Muon_plateau_9inch->FixParameter(1,Muon_plateau_9inch->GetParameter(1));
Muon_plateau_9inch->FixParameter(2,Muon_plateau_9inch->GetParameter(2));


****************************************
Minimizer is Linear / Migrad
Chi2                      =      25.1086
NDf                       =           14
a                         =      4.50639   +/-   0.0909626   
b                         =  -0.00896256   +/-   0.000355826 
c                         =  7.48002e-06   +/-   3.19713e-07 


In [46]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_9inch->Draw("");

3- Function for the queue at high energies betweenn 2700 and 4400 keVee. It is the sum of two exponential functions with a gaussian in the middle for the neutron peak.

In [47]:
TF1* Muon_queue_9inch_start = new TF1("Muon_queue_9inch_start", "expo(0)", 1800, 3000); 
Muon_queue_9inch_start->SetParameter(0, -10);
Muon_queue_9inch_start->SetParameter(1, -0.003);
h_SimuMuons_9inch->Fit("Muon_queue_9inch_start", "R");

TF1* Muon_queue_9inch_end = new TF1("Muon_queue_9inch_end", "expo(0)", 4500, 5500); 
Muon_queue_9inch_end->SetParameter(0, -10);
Muon_queue_9inch_end->SetParameter(1, -0.003);
h_SimuMuons_9inch->Fit("Muon_queue_9inch_end", "R");

TF1* Muon_queue_secn_9inch = new TF1("Muon_queue_secn_9inch", "expo(0)+gaus(2)+expo(5)", 1800, 5500); 
//Muon_queue_9inch->SetParNames("Norm", "slope", "Norm_NP", "mean_NP", "sigma_NP");
Muon_queue_secn_9inch->SetParameter(0, Muon_queue_9inch_start->GetParameter(0));
Muon_queue_secn_9inch->SetParameter(1, Muon_queue_9inch_start->GetParameter(1));
Muon_queue_secn_9inch->SetParameter(2, 0.011);
Muon_queue_secn_9inch->SetParameter(3, 3500);
Muon_queue_secn_9inch->SetParameter(4, 300);
Muon_queue_secn_9inch->SetParameter(5, Muon_queue_9inch_end->GetParameter(0));
Muon_queue_secn_9inch->SetParameter(6, Muon_queue_9inch_end->GetParameter(1));

Muon_queue_secn_9inch->SetParLimits(3, 3500, 3800);
Muon_queue_secn_9inch->SetParLimits(2, 0., 1000);
Muon_queue_secn_9inch->SetParLimits(4, 100, 600);
h_SimuMuons_9inch->Fit("Muon_queue_secn_9inch", "R");

Muon_queue_secn_9inch->FixParameter(0, Muon_queue_secn_9inch->GetParameter(0));
Muon_queue_secn_9inch->FixParameter(1, Muon_queue_secn_9inch->GetParameter(1));
Muon_queue_secn_9inch->FixParameter(2, Muon_queue_secn_9inch->GetParameter(2));
Muon_queue_secn_9inch->FixParameter(3, Muon_queue_secn_9inch->GetParameter(3));
Muon_queue_secn_9inch->FixParameter(4, Muon_queue_secn_9inch->GetParameter(4));
Muon_queue_secn_9inch->FixParameter(5, Muon_queue_secn_9inch->GetParameter(5));
Muon_queue_secn_9inch->FixParameter(6, Muon_queue_secn_9inch->GetParameter(6));

 FCN=23.788 FROM MIGRAD    STATUS=CONVERGED      47 CALLS          48 TOTAL
                     EDM=7.46729e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant     3.47119e+00   4.44522e-02   1.50933e-05   6.12001e-02
   2  Slope       -1.49667e-03   1.98044e-05   6.72417e-09   1.39587e+02
 FCN=22.7302 FROM MIGRAD    STATUS=CONVERGED      57 CALLS          58 TOTAL
                     EDM=2.08848e-09    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant     1.23356e+00   6.52534e-01   7.99608e-05   1.30895e-03
   2  Slope       -8.78275e-04   1.32453e-04   1.62307e-08   6.79749e+00
 FCN=94.0863 FROM HESSE     STATUS=OK             50 CALLS         768 TOTAL
                     EDM=5.810

In [48]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_9inch->Draw("");
Muon_queue_secn_9inch->Draw("SAME");
Muon_queue_9inch_end->SetLineColor(kBlue);
Muon_queue_9inch_end->Draw("SAME");
Muon_queue_9inch_start->SetLineColor(kBlue);
Muon_queue_9inch_start->Draw("SAME");

The final function is the sum of those three contributions linked by two step functions (cdf) one at low energy to link the plateau with the muon peak and one at high energies to link the muon peak to the queue.

In [49]:
Double_t Muons_9inch(Double_t* x, Double_t *par){
    Double_t par_cdf[2]= {par[3], par[4]};
    Double_t par_cdf2[2]= {par[5], par[6]};
    return (1-cdf(x, par_cdf))*par[0]*Muon_plateau_9inch->Eval(x[0])+cdf(x, par_cdf)*(1-cdf(x, par_cdf2))*par[1]*Muon_peak_9inch->Eval(x[0])+cdf(x, par_cdf2)*par[2]*Muon_queue_secn_9inch->Eval(x[0]);
}

In [50]:
TF1* Muon_shape_9inch = new TF1("Muon_shape_9inch", Muons_9inch, 150, 5500, 7);
Muon_shape_9inch->SetParNames("Norm_plateau", "Norm_muonpeak", "Norm_muonqueue", "pos cdf", "sigma cdf", "pos cdf2", "sigma cdf2");

Muon_shape_9inch->SetParameter(0, 1);
Muon_shape_9inch->SetParameter(1, 1);
Muon_shape_9inch->SetParameter(2, 1);

Muon_shape_9inch->SetParameter(3, 1000);
Muon_shape_9inch->SetParameter(4, 400);
Muon_shape_9inch->SetParLimits(4, 0, 500);
Muon_shape_9inch->SetParLimits(3, 800, 1400);
Muon_shape_9inch->SetParameter(5, 2900);
Muon_shape_9inch->SetParLimits(5, 2000, 6000);
Muon_shape_9inch->SetParameter(6, 400);
Muon_shape_9inch->SetParLimits(6, 0, 500);
h_SimuMuons_9inch->Fit("Muon_shape_9inch", "R0");

 FCN=242.936 FROM HESSE     STATUS=NOT POSDEF     68 CALLS         570 TOTAL
                     EDM=4.285e-07    STRATEGY= 1      ERR MATRIX NOT POS-DEF
  EXT PARAMETER                APPROXIMATE        STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_plateau   1.01653e+00   5.26949e-03   7.29666e-06  -2.81939e-02
   2  Norm_muonpeak   9.98064e-01   4.31544e-03   6.37838e-06  -2.61898e-02
   3  Norm_muonqueue   9.97383e-01   1.06003e-02   1.07613e-05  -3.02937e-02
   4  pos cdf      1.07184e+03   6.30472e+00   2.97912e-05   3.55590e-03
   5  sigma cdf    1.00737e+02   7.62630e+00   5.51022e-05   2.22877e-02
   6  pos cdf2     2.17003e+03   3.59229e+03   9.33561e-03  -1.19101e-04
   7  sigma cdf2   2.64334e+00   2.75685e+02   1.86799e-01   2.75264e-05


In [51]:
TCanvas* C11 = new TCanvas();
C11->Draw();
C11->SetLogy();
h_SimuMuons_9inch->Draw("");
Muon_shape_9inch->Draw("SAME");

The shapes of gammas and muons background contributions are fixed. The global background function is the sum of the two contributions with their weight as parameters.

In [52]:
Gamma_shape_9inch->FixParameter(1, Gamma_shape_9inch->GetParameter(1));
Gamma_shape_9inch->FixParameter(0, Gamma_shape_9inch->GetParameter(0));
Muon_shape_9inch->FixParameter(0, Muon_shape_9inch->GetParameter(0));
Muon_shape_9inch->FixParameter(1, Muon_shape_9inch->GetParameter(1));
Muon_shape_9inch->FixParameter(2, Muon_shape_9inch->GetParameter(2));
Muon_shape_9inch->FixParameter(3, Muon_shape_9inch->GetParameter(3));
Muon_shape_9inch->FixParameter(4, Muon_shape_9inch->GetParameter(4));
Muon_shape_9inch->FixParameter(5, Muon_shape_9inch->GetParameter(5));
Muon_shape_9inch->FixParameter(6, Muon_shape_9inch->GetParameter(6));

In [53]:
Double_t MuonsplusGammas_9inch(Double_t* x, Double_t *par){
    return par[0]*Muon_shape_9inch->Eval(x[0])+par[1]*Gamma_shape_9inch->Eval(x[0]);
}

Then, the signal is added to the background. 

### Neutron Peak

Fit of the neutron peak obtained in the simulation (cross check but not used to constrain the signal model). 

In [54]:
TF1* Neutron_peak_Gaus = new TF1("Neutron_peak", "[0]*TMath::Gaus(x, [1], [2])", 2500, 4500);
Neutron_peak_Gaus->SetParNames("Amplitude [Counts/d/keVee]", "#mu [keVee]", "#sigma [keVee]");
Neutron_peak_Gaus->SetParameter(0, 0.1);
Neutron_peak_Gaus->SetParameter(1, 3500);
Neutron_peak_Gaus->SetParameter(2, 300);

h_SimuNeutrons_9inch->Fit("Neutron_peak", "R");

 FCN=881.634 FROM MIGRAD    STATUS=CONVERGED     143 CALLS         144 TOTAL
                     EDM=9.11146e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Amplitude [Counts/d/keVee]   5.26643e-01   1.16705e-03   1.34406e-05  -2.01886e-01
   2  #mu [keVee]   3.49848e+03   5.37792e-01   7.76540e-03   6.77913e-04
   3  #sigma [keVee]   3.02518e+02   4.12325e-01   4.73472e-03  -5.64079e-04


In [55]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuNeutrons_9inch->Draw("");

In [56]:
TF1* plateau_Neutron = new TF1("plateau_Neutron", "[0]*x +[1]", 4500, 5500);
plateau_Neutron->SetParameter(0, 1e-2);
plateau_Neutron->SetParameter(1, 5500);

h_SimuNeutrons_9inch->Fit("plateau_Neutron", "R");

plateau_Neutron->FixParameter(0, plateau_Neutron->GetParameter(0));
plateau_Neutron->FixParameter(1, plateau_Neutron->GetParameter(1));

 FCN=26.5049 FROM MIGRAD    STATUS=CONVERGED      43 CALLS          44 TOTAL
                     EDM=3.25359e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  p0          -7.49497e-07   1.13517e-07   1.30927e-07  -1.42473e+05
   2  p1           4.41364e-03   5.74973e-04   1.65000e-02  -2.81287e+01


In [57]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuNeutrons_9inch->Draw("");

In [58]:
Double_t Neutron_PeakAndHighE_9inch(Double_t* x, Double_t *par){
    Double_t par_cdf[2]= {par[4], par[5]};
    return par[0]*TMath::Gaus(x[0], par[1], par[2])+cdf(x, par_cdf)*par[3]*plateau_Neutron->Eval(x[0]);
}

In [59]:
TF1* Neutron_shape = new TF1("Neutron_shape", "Neutron_PeakAndHighE_9inch", 1000, 5600, 6);
Neutron_shape->SetParameter(0, Neutron_peak_Gaus->GetParameter(0));
Neutron_shape->SetParameter(1, Neutron_peak_Gaus->GetParameter(1));
Neutron_shape->SetParameter(2, Neutron_peak_Gaus->GetParameter(2));
Neutron_shape->SetParameter(3, 1);
Neutron_shape->FixParameter(4, 4500);
Neutron_shape->FixParameter(5, 100);

h_SimuNeutrons_9inch->Fit("Neutron_shape", "R", "", 2000, 5600);

TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuNeutrons_9inch->Draw("");

Neutron_shape->FixParameter(0, Neutron_shape->GetParameter(0));
Neutron_shape->FixParameter(3, Neutron_shape->GetParameter(3));
Neutron_shape->FixParameter(4, Neutron_shape->GetParameter(4));
Neutron_shape->FixParameter(5, Neutron_shape->GetParameter(5));

 FCN=5355.42 FROM MIGRAD    STATUS=CONVERGED      96 CALLS          97 TOTAL
                     EDM=3.51859e-10    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  p0           5.25420e-01   1.16764e-03   3.30180e-05  -5.18585e-03
   2  p1           3.49761e+03   5.38390e-01   1.90970e-02   4.58675e-05
   3  p2           3.03331e+02   4.13977e-01   1.16245e-02  -1.89604e-05
   4  p3           8.40759e-01   4.56730e-02   1.62540e-03   1.25056e-04
   5  p4           4.50000e+03     fixed    
   6  p5           1.00000e+02     fixed    


The signal model is the sum of the two background contributions (gammas and muons) and a gaussian. It has 5 parameters : gamma weight, muon weight, neutron weight, neutron peak position and neutron peak width. 

Remark: given the contribution of neutrons at low energies and the kind of plateau before the neutron capture peak, it could be interesting to improve the model by including those parts of the neutron spectrum in the signal model function. 

In [60]:
Double_t SignalPlusBackground_9inch(Double_t* x, Double_t *par){
    Neutron_shape->SetParameter(1, par[3]);
    Neutron_shape->SetParameter(2, par[4]);
    return par[0]*Muon_shape_9inch->Eval(x[0])+par[1]*Gamma_shape_9inch->Eval(x[0])+par[2]*Neutron_shape->Eval(x[0]);
}

In [61]:
Double_t Gammas_9inch(Double_t* x, Double_t *par){
    return par[0]*Gamma_shape_9inch->Eval(x[0]);
}

In [62]:
Double_t Muons_9inch(Double_t* x, Double_t *par){
    return par[0]*Muon_shape_9inch->Eval(x[0]);
}

In [63]:
Double_t Neutrons_9inch(Double_t* x, Double_t *par){
    Neutron_shape->SetParameter(1, par[1]);
    Neutron_shape->SetParameter(2, par[2]);
    return par[0]*Neutron_shape->Eval(x[0]);
}

In [64]:
TF1* Sum_background_9inch = new TF1("Sum_background_9inch", MuonsplusGammas_9inch, 400, 6000, 2);
Sum_background_9inch->SetParNames("Norm_muons", "Norm_gammas");

In [65]:
TF1* Muon_background_9inch = new TF1("Muon_background_9inch", Muons_9inch, 50, 6000, 1);
Muon_background_9inch->SetParNames("Norm_muons");

In [66]:
TF1* Gamma_background_9inch = new TF1("Gamma_background_9inch", Gammas_9inch, 50, 6000, 1);
Gamma_background_9inch->SetParNames("Norm_gammas");

In [67]:
TF1* Neutron_signal_9inch = new TF1("Neutron_signal_9inch", Neutrons_9inch, 50, 6000, 3);
Gamma_background_9inch->SetParNames("Norm_Neutrons");

In [68]:
TF1* SignalandBackground_9inch = new TF1("SignalandBackground_9inch", SignalPlusBackground_9inch, 400, 5000, 5);
SignalandBackground_9inch->SetParNames("Norm_muons", "Norm_gammas", "Norm_Neutr", "Mean_gauss", "Sigma_gauss");

## Fit

Fitting procedure : the shapes of background contributions have been constrained by the fit of the simulations before. The weight of each contribution is fitted as well as the neutron peak (in shape and norm). <br>  <br> 
The number of events in the neutron peak are calculated as follow: <br>
<b>N_ev_tot</b> = The total number of events in the histogram in the peak region [2500, 4500 keVee]. The uncertainty is statistical only. <br>
<b>N_ev_bckg</b> = The integral of the background from fit result in the peak region. The uncertainty is obtained from the fit parameters errors on muon and gamma normalization.  <br>
<b>N_ev_in_neutron_peak</b> = N_ev_tot-N_ev_bckg with the error propagation from the two previous errors quoted.

### DCHut
Fit of the data at surface.

In [69]:
SignalandBackground_9inch->SetParameter(3, 3500);
SignalandBackground_9inch->SetParLimits(3, 3000, 4000);
SignalandBackground_9inch->SetParameter(2, 1);
if (SignalandBackground_9inch->GetParameter(4)==0) SignalandBackground_9inch->SetParameter(4, Resol_NP*3500);

TFitResultPtr r = hCal_DC_9inch->Fit(SignalandBackground_9inch, "S0", "", 500, 6000);

TMatrixD CovMat_DC = r->GetCovarianceMatrix();

//CovMat_DC.Print();

Double_t err_norm_NP_DC = sqrt(CovMat_DC(2,2));
Double_t norm_NP_DC = SignalandBackground_9inch->GetParameter(2);

Double_t err_norm_Bkg_DC = sqrt(CovMat_DC(0,0)+CovMat_DC(1,1)+2*CovMat_DC(0,1));
Double_t norm_Bckg_DC = SignalandBackground_9inch->GetParameter(0)+SignalandBackground_9inch->GetParameter(1);

Double_t Norm_mu_9_DC = SignalandBackground_9inch->GetParameter(0);
Double_t err_Norm_mu_9_DC = SignalandBackground_9inch->GetParError(0);

Sum_background_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(0));
Sum_background_9inch->SetParameter(1, SignalandBackground_9inch->GetParameter(1));

Muon_background_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(0));
Gamma_background_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(1));

Neutron_signal_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(2));
Neutron_signal_9inch->SetParameter(1, SignalandBackground_9inch->GetParameter(3));
Neutron_signal_9inch->SetParameter(2, SignalandBackground_9inch->GetParameter(4));

double Emin=3000;
double Emax = 4300;

Double_t N_ev_tot_DC = SignalandBackground_9inch->Integral(Emin, Emax);
Double_t N_ev_NP_DC = Neutron_signal_9inch->Integral(Emin, Emax);
Double_t err_N_ev_NP_DC = (err_norm_NP_DC/norm_NP_DC)*Neutron_signal_9inch->Integral(Emin, Emax);
Double_t N_ev_BKG_DC = Sum_background_9inch->Integral(Emin, Emax);
Double_t err_N_ev_BKG_DC = (err_norm_Bkg_DC/norm_Bckg_DC)*Sum_background_9inch->Integral(Emin, Emax);

Double_t err_N_ev_data_DC;
Double_t N_ev_data_DC = hCal_DC_9inch->IntegralAndError(hCal_DC_9inch->FindBin(Emin), hCal_DC_9inch->FindBin(Emax), err_N_ev_data_DC, "width");

Double_t err_N_ev_data_NP_DC = sqrt(err_N_ev_data_DC*err_N_ev_data_DC + err_N_ev_BKG_DC*err_N_ev_BKG_DC);
Double_t N_ev_data_NP_DC = N_ev_data_DC-N_ev_BKG_DC;

cout<<"\nChi2/ndf = "<<SignalandBackground_9inch->GetChisquare()<<"/"<<SignalandBackground_9inch->GetNDF()<<" = "<<SignalandBackground_9inch->GetChisquare()/SignalandBackground_9inch->GetNDF()<<endl;
cout<<"\nTotal N_ev in peak region = "<<N_ev_data_DC<<" ev/d +- "<<err_N_ev_data_DC<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from fit = "<<N_ev_NP_DC<<" ev/d +- "<<err_N_ev_NP_DC<<" ev/d (error from normalization error only!)"<<endl;
cout<<"N_ev in background = "<<N_ev_BKG_DC<<" ev/d +- "<<err_N_ev_BKG_DC<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from data - bckg = "<<N_ev_data_NP_DC<<" ev/d +- "<<err_N_ev_data_NP_DC<<" ev/d"<<endl;

SignalandBackground_9inch->FixParameter(4, SignalandBackground_9inch->GetParameter(4)); //Fix the sigma value of the neutron peak

 FCN=326.31 FROM MIGRAD    STATUS=CONVERGED     138 CALLS         139 TOTAL
                     EDM=5.25391e-08    STRATEGY= 1  ERROR MATRIX UNCERTAINTY   2.4 per cent
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   3.10583e-01   1.80859e-03  -2.60372e-06  -1.64137e-01
   2  Norm_gammas   7.96439e-01   8.68513e-03  -2.35820e-06  -4.36651e-02
   3  Norm_Neutr   3.42476e-01   8.16749e-03  -1.56969e-05  -4.09451e-02
   4  Mean_gauss   3.68545e+03   7.19641e+00  -5.70165e-06   3.34417e-03
   5  Sigma_gauss   3.37125e+02   7.80325e+00  -1.08124e-02  -2.67970e-05

Chi2/ndf = 326.31/110 = 2.96646

Total N_ev in peak region = 238.099 ev/d +- 2.63666 ev/d
N_ev in neutron peak from fit = 143.672 ev/d +- 3.42633 ev/d (error from normalization error only!)
N_ev in background = 92.141 ev/d +- 0.660004 ev/d
N_ev in neutron peak from data - bckg = 145.958 ev/d +- 2.71801 ev/d


In [70]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hCal_DC_9inch->Draw("");
SignalandBackground_9inch->SetLineColor(kBlack);
hCal_DC_9inch->GetYaxis()->SetRangeUser(1e-4, 10);
Sum_background_9inch->SetLineColor(kBlue);
Sum_background_9inch->Draw("RSAME");
Muon_background_9inch->SetLineColor(kGreen);
Gamma_background_9inch->SetLineColor(kRed);
Muon_background_9inch->Draw("RSAME");
Gamma_background_9inch->Draw("RSAME");
Sum_background_9inch->Draw("RSAME");
SignalandBackground_9inch->Draw("RSAME");
Neutron_signal_9inch->SetLineColor(kMagenta);
Neutron_signal_9inch->Draw("RSAME");

TLegend* leg0 = new TLegend(0.6, 0.7, 0.89, 0.89);
leg0->AddEntry(Sum_background_9inch, "Background");
leg0->AddEntry(SignalandBackground_9inch, "Signal and Bckg");
leg0->AddEntry(Neutron_signal_9inch, "Neutron Signal");
leg0->AddEntry(Muon_background_9inch, "Muon Bckg");
leg0->AddEntry(Gamma_background_9inch, "Gamma Bckg");
leg0->Draw("SAME");
leg0->SetLineWidth(0);

TCanvas* C2 = new TCanvas("cRes_DC_9inch", "cRes_DC_9inch", 1.175*C->GetWw(), 0.6*C->GetWh());
C2->Draw();
TPad *p1 = new TPad("p1","p1",0.,0.02,0.795,1.);
p1->Draw();
p1->cd();
p1->SetRightMargin(0.03);
p1->SetBottomMargin(0.2);

histosRes_DC_9inch = Residuals_vec(hCal_DC_9inch, SignalandBackground_9inch, 500, 6000, true);
hRes_DC_9inch=histosRes_DC_9inch[0];
hRes_DC_9inch->GetYaxis()->SetTitle("Residuals [%]");
hRes_DC_9inch->GetYaxis()->SetTitleSize(1.9*hCal_DC_9inch->GetYaxis()->GetTitleSize());
hRes_DC_9inch->GetXaxis()->SetTitleSize(1.9*hCal_DC_9inch->GetXaxis()->GetTitleSize());
hRes_DC_9inch->GetYaxis()->SetLabelSize(1.9*hCal_DC_9inch->GetYaxis()->GetLabelSize());
hRes_DC_9inch->GetXaxis()->SetLabelSize(1.9*hCal_DC_9inch->GetXaxis()->GetLabelSize());
hRes_DC_9inch->Draw("");

h_10pc = (TH1D*) hRes_DC_9inch->Clone();
for (int i =1; i<=h_10pc->GetNbinsX(); i++){
    h_10pc->SetBinContent(i, 0);
    h_10pc->SetBinError(i, 10);
}
h_10pc->SetLineColorAlpha(kOrange+1, 0.2);
h_10pc->SetMarkerColorAlpha(kOrange+1, 0.2);
h_10pc->SetFillColorAlpha(kOrange+1, 0.2);
h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10%");
leg->Draw("SAME");
leg->SetLineWidth(0);


C2->cd();
TPad *p2 = new TPad("p2","p2",0.795,0.02,1.,1.);
p2->Draw();
p2->cd();
p2->SetLeftMargin(0.15);
p2->SetBottomMargin(0.2);

hRedRes_DC_9inch=histosRes_DC_9inch[1];
hRedRes_DC_9inch->Draw("");
hRedRes_DC_9inch->GetXaxis()->SetTitle("Residuals [#sigma]");
hRedRes_DC_9inch->GetYaxis()->SetTitleSize(3.*hCal_DC_9inch->GetYaxis()->GetTitleSize());
hRedRes_DC_9inch->GetXaxis()->SetTitleSize(2.7*hCal_DC_9inch->GetXaxis()->GetTitleSize());
hRedRes_DC_9inch->GetXaxis()->SetTitleOffset(0.7);
hRedRes_DC_9inch->GetYaxis()->SetLabelSize(3.*hCal_DC_9inch->GetYaxis()->GetLabelSize());
hRedRes_DC_9inch->GetXaxis()->SetLabelSize(2.7*hCal_DC_9inch->GetXaxis()->GetLabelSize());
hRedRes_DC_9inch->GetXaxis()->SetNdivisions(5);

Good agreement in shape of the fit, but the muon peak seems to not be exactly at the same position as in the simulation... (quenching?, not good calibration?) 

### VNS
Fit of the data in the VNS. <br>
For the VNS, the width of the neutron peak is fixed.

In [71]:
TFitResultPtr r_9_VNS = hCal_VNS_9inch->Fit(SignalandBackground_9inch, "SR0", "", 1100, 6000);
r_9_VNS = hCal_VNS_9inch->Fit(SignalandBackground_9inch, "SR0", "", 1100, 6000);

TMatrixD CovMat_VNS = r_9_VNS->GetCovarianceMatrix();

//CovMat_VNS.Print();

Double_t err_norm_NP_VNS = sqrt(CovMat_VNS(2,2));
Double_t norm_NP_VNS = SignalandBackground_9inch->GetParameter(2);

Double_t err_norm_Bkg_VNS = sqrt(CovMat_VNS(0,0)+CovMat_VNS(1,1)+2*CovMat_VNS(0,1));
Double_t norm_Bckg_VNS = SignalandBackground_9inch->GetParameter(0)+SignalandBackground_9inch->GetParameter(1);

Double_t Norm_mu_9_VNS = SignalandBackground_9inch->GetParameter(0);
Double_t err_Norm_mu_9_VNS = SignalandBackground_9inch->GetParError(0);

Sum_background_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(0));
Sum_background_9inch->SetParameter(1, SignalandBackground_9inch->GetParameter(1));

Muon_background_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(0));
Gamma_background_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(1));

Neutron_signal_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(2));
Neutron_signal_9inch->SetParameter(1, SignalandBackground_9inch->GetParameter(3));
Neutron_signal_9inch->SetParameter(2, SignalandBackground_9inch->GetParameter(4));


Double_t N_ev_tot_VNS = SignalandBackground_9inch->Integral(Emin, Emax);
Double_t N_ev_NP_VNS = Neutron_signal_9inch->Integral(Emin, Emax);
Double_t err_N_ev_NP_VNS = (err_norm_NP_VNS/norm_NP_VNS)*Neutron_signal_9inch->Integral(Emin, Emax);
Double_t N_ev_BKG_VNS = Sum_background_9inch->Integral(Emin, Emax);
Double_t err_N_ev_BKG_VNS = (err_norm_Bkg_VNS/norm_Bckg_VNS)*Sum_background_9inch->Integral(Emin, Emax);

Double_t err_N_ev_data_VNS;
Double_t N_ev_data_VNS = hCal_VNS_9inch->IntegralAndError(hCal_VNS_9inch->FindBin(Emin), hCal_VNS_9inch->FindBin(Emax), err_N_ev_data_VNS, "width");

Double_t err_N_ev_data_NP_VNS = sqrt(err_N_ev_data_VNS*err_N_ev_data_VNS + err_N_ev_BKG_VNS*err_N_ev_BKG_VNS);
Double_t N_ev_data_NP_VNS = N_ev_data_VNS-N_ev_BKG_VNS;

cout<<"\nChi2/ndf = "<<SignalandBackground_9inch->GetChisquare()<<"/"<<SignalandBackground_9inch->GetNDF()<<" = "<<SignalandBackground_9inch->GetChisquare()/SignalandBackground_9inch->GetNDF()<<endl;
cout<<"\nTotal N_ev in peak region = "<<N_ev_tot_VNS<<" ev/d +- "<<err_N_ev_data_VNS<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from fit = "<<N_ev_NP_VNS<<" ev/d +- "<<err_N_ev_NP_VNS<<" ev/d (error from normalization error only!)"<<endl;
cout<<"N_ev in background = "<<N_ev_BKG_DC<<" ev/d +- "<<err_N_ev_BKG_VNS<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from data - bckg = "<<N_ev_data_NP_VNS<<" ev/d +- "<<err_N_ev_data_NP_VNS<<" ev/d"<<endl;

 FCN=118.426 FROM MIGRAD    STATUS=CONVERGED     161 CALLS         162 TOTAL
                     EDM=2.65933e-09    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   1.58232e-01   1.70042e-03   5.66136e-06   2.18361e-03
   2  Norm_gammas   1.16357e+00   3.46346e-02   1.19429e-04   2.14602e-03
   3  Norm_Neutr   1.62693e-02   2.35125e-03   1.10583e-05   2.25975e-03
   4  Mean_gauss   3.78862e+03   5.97289e+01   7.40003e-04   1.82172e-05
   5  Sigma_gauss   3.37125e+02     fixed    
 FCN=118.426 FROM MIGRAD    STATUS=CONVERGED      51 CALLS          52 TOTAL
                     EDM=1.57151e-09    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   1.58232e-01   1.70042e-03   5.66136e-06 

In [72]:
TCanvas* C12 = new TCanvas();
C12->Draw();
C12->SetLogy();
hCal_VNS_9inch->Draw("");
Sum_background_9inch->SetLineColor(kBlue);
Muon_background_9inch->SetLineColor(kGreen);
Gamma_background_9inch->SetLineColor(kRed);
Muon_background_9inch->Draw("RSAME");
Gamma_background_9inch->Draw("RSAME");
Sum_background_9inch->Draw("RSAME");
SignalandBackground_9inch->Draw("RSAME");
Neutron_signal_9inch->SetLineColor(kMagenta);
Neutron_signal_9inch->Draw("RSAME");

TLegend* leg0 = new TLegend(0.6, 0.7, 0.89, 0.89);
leg0->AddEntry(Sum_background_9inch, "Background");
leg0->AddEntry(SignalandBackground_9inch, "Signal and Bckg");
leg0->AddEntry(Neutron_signal_9inch, "Neutron Signal");
leg0->AddEntry(Muon_background_9inch, "Muon Bckg");
leg0->AddEntry(Gamma_background_9inch, "Gamma Bckg");
leg0->Draw("SAME");
leg0->SetLineWidth(0);

TCanvas* C2 = new TCanvas("cRes_VNS_9inch", "cRes_VNS_9inch", 1.175*C->GetWw(), 0.6*C->GetWh());
C2->Draw();
TPad *p1 = new TPad("p1","p1",0.,0.02,0.795,1.);
p1->Draw();
p1->cd();
p1->SetRightMargin(0.03);
p1->SetBottomMargin(0.2);

histosRes_VNS_9inch = Residuals_vec(hCal_VNS_9inch, SignalandBackground_9inch, 1100, 6000, true);
hRes_VNS_9inch=histosRes_VNS_9inch[0];
hRes_VNS_9inch->GetYaxis()->SetTitle("Residuals [%]");
hRes_VNS_9inch->GetYaxis()->SetTitleSize(1.9*hCal_VNS_9inch->GetYaxis()->GetTitleSize());
hRes_VNS_9inch->GetXaxis()->SetTitleSize(1.9*hCal_VNS_9inch->GetXaxis()->GetTitleSize());
hRes_VNS_9inch->GetYaxis()->SetLabelSize(1.9*hCal_VNS_9inch->GetYaxis()->GetLabelSize());
hRes_VNS_9inch->GetXaxis()->SetLabelSize(1.9*hCal_VNS_9inch->GetXaxis()->GetLabelSize());
hRes_VNS_9inch->Draw("");

h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10%");
leg->Draw("SAME");
leg->SetLineWidth(0);


C2->cd();
TPad *p2 = new TPad("p2","p2",0.795,0.02,1.,1.);
p2->Draw();
p2->cd();
p2->SetLeftMargin(0.15);
p2->SetBottomMargin(0.2);

hRedRes_VNS_9inch=histosRes_VNS_9inch[1];
hRedRes_VNS_9inch->Draw("");
hRedRes_VNS_9inch->GetXaxis()->SetTitle("Residuals [#sigma]");
hRedRes_VNS_9inch->GetYaxis()->SetTitleSize(3.*hCal_VNS_9inch->GetYaxis()->GetTitleSize());
hRedRes_VNS_9inch->GetXaxis()->SetTitleSize(2.7*hCal_VNS_9inch->GetXaxis()->GetTitleSize());
hRedRes_VNS_9inch->GetXaxis()->SetTitleOffset(0.7);
hRedRes_VNS_9inch->GetYaxis()->SetLabelSize(3.*hCal_VNS_9inch->GetYaxis()->GetLabelSize());
hRedRes_VNS_9inch->GetXaxis()->SetLabelSize(2.7*hCal_VNS_9inch->GetXaxis()->GetLabelSize());
hRedRes_VNS_9inch->GetXaxis()->SetNdivisions(5);

### Calibration Check

The neutron peak obtained in the DCHut is fitted locally to check the sigma value obtained and the calibration

In [73]:
Neutron_peak_Gaus->SetParameter(0, 0.1);
Neutron_peak_Gaus->SetParameter(1, 3500);
Neutron_peak_Gaus->SetParameter(2, 40*Cal_factor);

hCal_DC_9inch->Fit(Neutron_peak_Gaus, "", "", 3000, 4000);
Double_t new_cal_DC = 3500.*Cal_factor/Neutron_peak_Gaus->GetParameter(1);

 FCN=77.7416 FROM MIGRAD    STATUS=CONVERGED      90 CALLS          91 TOTAL
                     EDM=6.8144e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Amplitude [Counts/d/keVee]   2.41172e-01   4.09406e-03   1.24303e-05   3.87926e-01
   2  #mu [keVee]   3.60553e+03   1.26084e+01   4.60140e-02   1.12454e-06
   3  #sigma [keVee]   5.03881e+02   2.13527e+01   5.74967e-02   5.59900e-05


In [74]:
TCanvas* C11 = new TCanvas();
C11->Draw();
C11->SetLogy();
hCal_DC_9inch->Draw("");

Use the result of the peak position local fit of the gaussian to calibrate "correctly" the run (and put the neutron peak at 3.5 MeVee and compare the two calibrations.

In [75]:
TH1D* hnewCal_DC_9inch = Calibrate_histo(h_DC_9inch_sum, new_cal_DC, Form("%s_New_keVee", h_DC_9inch_sum->GetTitle()));

In [76]:
TCanvas* C12 = new TCanvas();
C12->Draw();
C12->SetLogy();
hCal_DC_9inch->Draw("");
hnewCal_DC_9inch->SetLineColor(kRed);
hnewCal_DC_9inch->Draw("RSAME");

In [77]:
TH1D* hMuonCal_DC_9inch = Calibrate_histo(h_DC_9inch_sum, 1./1.15*new_cal_DC, Form("%s_MuonCal_keVee", h_DC_9inch_sum->GetTitle()));

In [78]:
TCanvas* C12 = new TCanvas();
C12->Draw();
C12->SetLogy();
hCal_DC_9inch->Draw("");
hMuonCal_DC_9inch->SetLineColor(kRed);
hMuonCal_DC_9inch->Draw("RSAME");

The two calibrations show a small shift of the neutron peak. The choice is made to keep the first calibration as the accurate one and leave the peak postion as a free parameter in the signal fit. The width of the peak will be set free for fit at surface where the peak is significant and then fixed for the fits on VNS data.

## Peak position stability

Appendix: Check the stability of the peak position in the VNS.

In [79]:
TH1D* hCal_VNS_9inch_1 = Calibrate_histo(h_VNS_9inch_1, Cal_factor, Form("%s_keVee", h_VNS_9inch_1->GetTitle()));

In [80]:
TH1D* hCal_VNS_9inch_2 = Calibrate_histo(h_VNS_9inch_2, Cal_factor, Form("%s_keVee", h_VNS_9inch_2->GetTitle()));

In [81]:
TH1D* hCal_VNS_9inch_3 = Calibrate_histo(h_VNS_9inch_3, Cal_factor, Form("%s_keVee", h_VNS_9inch_3->GetTitle()));

In [82]:
hCal_VNS_9inch_1->Fit(SignalandBackground_9inch, "R", "", 400, 5000);

 FCN=153.764 FROM MIGRAD    STATUS=CONVERGED     163 CALLS         164 TOTAL
                     EDM=3.38665e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   1.31175e-01   2.04439e-03   1.06744e-05  -1.38065e-02
   2  Norm_gammas   1.05197e+00   1.04611e-02   5.72564e-05  -1.71647e-02
   3  Norm_Neutr   1.40322e-02   4.73492e-03   2.67993e-05  -3.71025e-02
   4  Mean_gauss   3.44846e+03   9.21665e+01   1.11530e-03  -1.49969e-04
   5  Sigma_gauss   3.37125e+02     fixed    


In [83]:
hCal_VNS_9inch_2->Fit(SignalandBackground_9inch, "R", "", 400, 5000);

 FCN=137.536 FROM MIGRAD    STATUS=CONVERGED     126 CALLS         127 TOTAL
                     EDM=3.18052e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   1.74755e-01   2.21984e-03   1.11569e-05  -5.97187e-02
   2  Norm_gammas   1.02946e+00   1.06048e-02   5.47762e-05  -9.09964e-03
   3  Norm_Neutr   1.09946e-02   4.15789e-03   2.26080e-05   4.86403e-02
   4  Mean_gauss   3.84192e+03   1.04730e+02   1.63326e-03   1.28758e-04
   5  Sigma_gauss   3.37125e+02     fixed    


In [84]:
hCal_VNS_9inch_3->Fit(SignalandBackground_9inch, "R", "", 400, 5000);

 FCN=168.453 FROM MIGRAD    STATUS=CONVERGED     101 CALLS         102 TOTAL
                     EDM=4.05192e-09    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   1.79318e-01   1.59687e-03   8.91519e-06   1.42985e-02
   2  Norm_gammas   1.04124e+00   7.62235e-03   4.35272e-05  -9.23289e-03
   3  Norm_Neutr   1.65407e-02   2.91772e-03   1.73315e-05  -2.51250e-03
   4  Mean_gauss   3.95802e+03   6.89538e+01   2.13375e-03   7.28879e-05
   5  Sigma_gauss   3.37125e+02     fixed    


The peak position seems to drift a little... Since the fit is converging in each run separatly, maybe it could be interesting to recalibrate individually the spectra to reduce the spreading of the peak and increase a bit its significance.

# Analysis of the 8 inches sphere

An analogous procedure is applied to the 8 inches sphere data

## Calibration

The neutron capture peak positions with the 8 inches and the 9 inches sphere was noticed to not be exactly the same. So another calibration factor is defined for the 8 inches data. 

In [85]:
TH1D* h_Cal_8inch = Put_data_in_histo("Measures@TUM/03-14_Cf252_LMU_BS-A-08_2h.dat", 2*24*3600., "8inch with Cf252 n source");
h_Cal_8inch->Rebin(4);
h_Cal_8inch->Scale(1/4.);


*******************************************************
Measures@TUM/03-14_Cf252_LMU_BS-A-08_2h.dat


In [86]:
h_Cal_8inch->Fit("Neutron_peak_MCA", "R");

Double_t Cal_factor_8inch = 3500./(Neutron_peak_Gaus_MCA->GetParameter(1)); //Neutron peak assumed to be at 3500keVee
Double_t err_Cal_factor_8inch = (Neutron_peak_Gaus_MCA->GetParError(1))/(Neutron_peak_Gaus_MCA->GetParameter(1))*Cal_factor_8inch; //Neutron peak assumed to be at 3500keVee

cout<<"\nCalibration for the 9inch sphere = "<<Cal_factor<<" +- "<< err_Cal_factor<<" keV/MCA"<<endl;
cout<<"Calibration for the 8inch sphere = "<<Cal_factor_8inch<<" +- "<< err_Cal_factor_8inch<<" keV/MCA"<<endl;

 FCN=45.4618 FROM MIGRAD    STATUS=CONVERGED      79 CALLS          80 TOTAL
                     EDM=3.77299e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Amplitude [Counts/MCA]   2.77512e+00   1.96451e-01   4.72878e-04  -1.60010e-04
   2  #mu [MCA]    3.29580e+02   1.55335e+00   4.86764e-03  -1.75059e-04
   3  #sigma [MCA]   2.77531e+01   1.43837e+00   3.35005e-03  -1.46485e-04

Calibration for the 9inch sphere = 10.7059 +- 0.0236396 keV/MCA
Calibration for the 8inch sphere = 10.6196 +- 0.0500515 keV/MCA


The calibration factors seems not so differents, but are still not compatible => Check if it is expected from simulation?

In [87]:
TCanvas* C8 = new TCanvas();
C8->Draw();
C8->SetLogy();
h_Cal_8inch->Draw();

## Simulation and background model

### Gammas Background

In [88]:
TH1D* h_SimuGamma_8inch = Put_simu_in_histo("Simulations/Env_Gammas/BS_D08/Analyzer_T_run01-06.root", "8 inches environmental gammas", nbins, hEmin, hEmax, 1.20e10, 3.3, 6., false);

  Primary Entries:         1790299
  Secondary Entries:       1806637
  Generated primaries:  12000000000
  Equivalent time:      2272727 s (26.305 d)
 Nb of primary analysed: 1790299
 Nb of events quenched : 0


Gamma background with the two exponentials

In [89]:
TF1* Gamma_shape_8inch = new TF1("Gamma_shape_8inch", Gammas, 300, 4000, 4);
Gamma_shape_8inch->SetParNames("Norm_expo1", "Norm_expo2", "pos cdf", "sigma cdf");
Gamma_shape_8inch->SetParameter(2, 200);
Gamma_shape_8inch->SetParLimits(2, 100, 1000);
Gamma_shape_8inch->SetParameter(3, 200);
h_SimuGamma_8inch->Fit("Gamma_shape_8inch", "R");

Gamma_shape_8inch->FixParameter(0, Gamma_shape_8inch->GetParameter(0));
Gamma_shape_8inch->FixParameter(1, Gamma_shape_8inch->GetParameter(1));
Gamma_shape_8inch->FixParameter(2, Gamma_shape_8inch->GetParameter(2));
Gamma_shape_8inch->FixParameter(3, Gamma_shape_8inch->GetParameter(3));

 FCN=226.51 FROM MIGRAD    STATUS=CONVERGED     335 CALLS         336 TOTAL
                     EDM=1.57503e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_expo1   1.24751e+01   6.90729e+00   7.61908e-04   9.60195e-04
   2  Norm_expo2   1.02843e+00   7.43173e-03   3.75502e-05  -5.45743e-03
   3  pos cdf      2.30348e+02   7.67982e+01   1.85928e-05   3.93585e-02
   4  sigma cdf    1.28317e+02   2.39543e+01   5.33499e-03   1.02391e-04


In [90]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuGamma_8inch->Draw();

### Muons background

In [91]:
TH1D* h_SimuMuons_8inch = Put_simu_in_histo("Simulations/Atm_Muons/BS_D08/Analyzer_T_run01-12.root", "8 inches atmospheric muons",nbins, hEmin, hEmax, 8e7, 0.019, 6.);

  Primary Entries:          502660
  Secondary Entries:        567025
  Generated primaries:  80000000
  Equivalent time:      2631579 s (30.458 d)
 Nb of primary analysed: 502660
 Nb of events quenched : 13


In [92]:
TH1D* h_SimuMuons_8inch_1MeV = Put_simu_in_histo("Simulations/Atm_Muons/BS_D08/Analyzer_T_run01-12.root", "8 inches - atmospheric muons (with MV 1 MeV thr)", nbins, hEmin, hEmax,  9.60e8, 0.019, 1.);

TH1D* h_SimuMuons_8inch_5MeV = Put_simu_in_histo("Simulations/Atm_Muons/BS_D08/Analyzer_T_run01-12.root", "8 inches - atmospheric muons (with MV 5 MeV thr)", nbins, hEmin, hEmax,  9.60e8, 0.019, 5.);

TH1D* h_SimuMuons_8inch_7MeV = Put_simu_in_histo("Simulations/Atm_Muons/BS_D08/Analyzer_T_run01-12.root", "8 inches - atmospheric muons (with MV 7 MeV thr)", nbins, hEmin, hEmax,  9.60e8, 0.019, 7.);

TCanvas *C = new TCanvas();
C->Draw();
h_SimuMuons_8inch_1MeV->SetLineColor(kBlue);
h_SimuMuons_8inch_5MeV->SetLineColor(kRed);
h_SimuMuons_8inch_7MeV->SetLineColor(kMagenta);
h_SimuMuons_8inch_1MeV->Draw("HIST");
h_SimuMuons_8inch_5MeV->Draw("HIST SAME");
h_SimuMuons_8inch_7MeV->Draw("HIST SAME");

  Primary Entries:          502660
  Secondary Entries:        567025
  Generated primaries:  960000000
  Equivalent time:      31578947 s (365.497 d)
 Nb of primary analysed: 502660
 Nb of events quenched : 13
  Primary Entries:          502660
  Secondary Entries:        567025
  Generated primaries:  960000000
  Equivalent time:      31578947 s (365.497 d)
 Nb of primary analysed: 502660
 Nb of events quenched : 13
  Primary Entries:          502660
  Secondary Entries:        567025
  Generated primaries:  960000000
  Equivalent time:      31578947 s (365.497 d)
 Nb of primary analysed: 502660
 Nb of events quenched : 13


Muon Background: 1- Muons Peak

In [93]:
TF1* Muon_peak_8inch = new TF1("Muon_peak_8inch", "landau", 1100, 2200); //Landau in muon peak region
Muon_peak_8inch->SetParNames("Amplitude_mu []", "MPV [keVee]", "[Sigma [keVee]]");
Muon_peak_8inch->SetParameters(1,1200,100);
h_SimuMuons_8inch->Fit("Muon_peak_8inch", "R");

Muon_peak_8inch->FixParameter(0,Muon_peak_8inch->GetParameter(0));
Muon_peak_8inch->FixParameter(1,Muon_peak_8inch->GetParameter(1));
Muon_peak_8inch->FixParameter(2,Muon_peak_8inch->GetParameter(2));

 FCN=65.4674 FROM MIGRAD    STATUS=CONVERGED     118 CALLS         119 TOTAL
                     EDM=7.52872e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Amplitude_mu []   1.56104e+01   8.66926e-02   2.35531e-04  -6.09487e-03
   2  MPV [keVee]   1.39007e+03   4.01658e+00   1.31048e-02  -1.42862e-05
   3  [Sigma [keVee]]   2.47352e+02   3.01982e+00   9.25530e-06  -8.21024e-02


In [94]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_8inch->Draw();

2- Muon Plateau

In [95]:
TF1* Muon_plateau_8inch = new TF1("Muon_plateau_8inch", "expo+pol2(2)", 250, 1200); 
Muon_plateau_8inch->SetParNames("a", "b", "c", "d", "e");
h_SimuMuons_8inch->Fit("Muon_plateau_8inch", "R");

 FCN=31.0088 FROM HESSE     STATUS=NOT POSDEF     31 CALLS         535 TOTAL
                     EDM=6.04322e-07    STRATEGY= 1      ERR MATRIX NOT POS-DEF
  EXT PARAMETER                APPROXIMATE        STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  a            4.03656e-01   5.42917e-02   2.82191e-06   1.30935e-01
   2  b            4.44107e-06   8.14328e-05   3.83814e-09   1.29386e+02
   3  c            4.58569e-01   8.13357e-02   4.24260e-06   8.70657e-02
   4  d           -2.28800e-03   1.22270e-04   5.77842e-09   8.58559e+01
   5  e            2.39538e-06   8.11321e-08   6.46248e-12   8.85697e+04


In [96]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_8inch->Draw();

3- Muon queue

In [97]:
TF1* Muon_queue_8inch_start = new TF1("Muon_queue_8inch_start", "expo(0)", 1800, 4000); 
Muon_queue_8inch_start->SetParameter(0, -10);
Muon_queue_8inch_start->SetParameter(1, -0.003);
h_SimuMuons_8inch->Fit("Muon_queue_8inch_start", "R");

TF1* Muon_queue_8inch_end = new TF1("Muon_queue_8inch_end", "expo(0)", 4000, 5500); 
Muon_queue_8inch_end->SetParameter(0, -10);
Muon_queue_8inch_end->SetParameter(1, -0.003);
h_SimuMuons_8inch->Fit("Muon_queue_8inch_end", "R");

TF1* Muon_queue_8inch = new TF1("Muon_queue_8inch", "expo(0)+expo(2)", 1800, 5500); 
//Muon_queue_9inch->SetParNames("Norm", "slope", "Norm_NP", "mean_NP", "sigma_NP");
Muon_queue_8inch->SetParameter(0, Muon_queue_8inch_start->GetParameter(0));
Muon_queue_8inch->SetParameter(1, Muon_queue_8inch_start->GetParameter(1));
Muon_queue_8inch->SetParameter(2, Muon_queue_8inch_end->GetParameter(0));
Muon_queue_8inch->SetParameter(3, Muon_queue_8inch_end->GetParameter(1));

h_SimuMuons_8inch->Fit("Muon_queue_8inch", "R");

Muon_queue_8inch->FixParameter(0, Muon_queue_8inch->GetParameter(0));
Muon_queue_8inch->FixParameter(1, Muon_queue_8inch->GetParameter(1));
Muon_queue_8inch->FixParameter(2, Muon_queue_8inch->GetParameter(2));
Muon_queue_8inch->FixParameter(3, Muon_queue_8inch->GetParameter(3));

 FCN=161.409 FROM MIGRAD    STATUS=CONVERGED      53 CALLS          54 TOTAL
                     EDM=4.91232e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant     3.05002e+00   2.61523e-02   3.22345e-05  -1.87863e-01
   2  Slope       -1.38012e-03   1.06350e-05   1.31084e-08  -4.35173e+02
 FCN=48.2122 FROM MIGRAD    STATUS=CONVERGED      51 CALLS          52 TOTAL
                     EDM=2.47386e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant     1.60246e+00   2.43315e-01   7.08628e-05   1.80697e-02
   2  Slope       -9.76890e-04   5.31238e-05   1.54702e-08   9.36830e+01
 FCN=106.325 FROM MIGRAD    STATUS=CONVERGED     291 CALLS         292 TOTAL
                     EDM=3.63

In [98]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_8inch->Draw("");
Muon_queue_8inch_end->SetLineColor(kBlue);
Muon_queue_8inch_end->Draw("SAME");
Muon_queue_8inch_start->SetLineColor(kBlue);
Muon_queue_8inch_start->Draw("SAME");
Muon_queue_8inch->Draw("SAME");

Total muon function

In [99]:
Double_t Muons_8inch(Double_t* x, Double_t *par){
    Double_t par_cdf[2]= {par[3], par[4]};
    Double_t par_cdf2[2]= {par[5], par[6]};
    return (1-cdf(x, par_cdf))*par[0]*Muon_plateau_8inch->Eval(x[0])+cdf(x, par_cdf)*(1-cdf(x, par_cdf2))*par[1]*Muon_peak_8inch->Eval(x[0])+cdf(x, par_cdf2)*par[2]*Muon_queue_8inch->Eval(x[0]);
}

In [100]:
TF1* Muon_shape_8inch = new TF1("Muon_shape_8inch", Muons_8inch, 200, 5500, 7);
Muon_shape_8inch->SetParNames("Norm_plateau", "Norm_muonpeak", "Norm_muonplateau","pos cdf", "sigma cdf", "pos cdf2", "sigma cdf2");
Muon_shape_8inch->SetParameter(0, 1);
Muon_shape_8inch->SetParameter(1, 1);
Muon_shape_8inch->SetParameter(2, 1);
Muon_shape_8inch->SetParameter(3, 900);
Muon_shape_8inch->SetParameter(4, 100);
Muon_shape_8inch->SetParameter(5, 3250);
Muon_shape_8inch->SetParameter(6, 100);
Muon_shape_8inch->SetParLimits(3, 800, 1200);
Muon_shape_8inch->SetParLimits(5, 3200, 3400);
h_SimuMuons_8inch->Fit("Muon_shape_8inch", "R");

 FCN=303.362 FROM MIGRAD    STATUS=FAILED        597 CALLS         598 TOTAL
                     EDM=2.65593e+08    STRATEGY= 1      ERR MATRIX NOT POS-DEF
  EXT PARAMETER                APPROXIMATE        STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_plateau   9.30181e-01   5.89931e-02  -0.00000e+00  -1.56323e+01
   2  Norm_muonpeak   1.00429e+00   2.08946e-02   0.00000e+00   1.98232e+01
   3  Norm_muonplateau   7.07573e-01   4.70949e-02  -0.00000e+00   7.85043e+00
   4  pos cdf      1.19749e+03   3.06756e+02  -0.00000e+00   4.30391e+00
   5  sigma cdf    2.41380e+00   1.67476e-04   0.00000e+00  -1.94619e+08
   6  pos cdf2     3.39990e+03   1.29249e+02   0.00000e+00  -7.17206e-02
   7  sigma cdf2   1.21456e+03   1.52442e+02   0.00000e+00  -2.12622e-03


Warning in <Fit>: Abnormal termination of minimization.


In [101]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_8inch->Draw();

In [102]:
Muon_shape_8inch->FixParameter(0, 1);
Muon_shape_8inch->FixParameter(0, Muon_shape_8inch->GetParameter(0));
Muon_shape_8inch->FixParameter(1, Muon_shape_8inch->GetParameter(1));
Muon_shape_8inch->FixParameter(2, Muon_shape_8inch->GetParameter(2));
Muon_shape_8inch->FixParameter(3, Muon_shape_8inch->GetParameter(3));

### Model background and signal

Background: Gammas + Muons with parameters their respective weights. <br>
Signal: Gammas + Muons + Gaussian

In [103]:
Double_t MuonsplusGammas_8inch(Double_t* x, Double_t *par){
    return par[0]*Muon_shape_8inch->Eval(x[0])+par[1]*Gamma_shape_8inch->Eval(x[0]);
}

In [104]:
Double_t Muons_8inch(Double_t* x, Double_t *par){
    return par[0]*Muon_shape_8inch->Eval(x[0]);
}

In [105]:
Double_t Gammas_8inch(Double_t* x, Double_t *par){
    return par[0]*Gamma_shape_8inch->Eval(x[0]);
}

In [106]:
Double_t SignalPlusBackground_8inch(Double_t* x, Double_t *par){
    return par[0]*Muon_shape_8inch->Eval(x[0])+par[1]*Gamma_shape_8inch->Eval(x[0])+par[2]*TMath::Gaus(x[0], par[3], par[4]);
}

In [107]:
TF1* Sum_background_8inch = new TF1("Sum_background_8inch", MuonsplusGammas_8inch, 50, 5200, 2);
Sum_background_8inch->SetParNames("Norm_muons", "Norm_gammas");

In [108]:
TF1* Muon_background_8inch = new TF1("Muon_background_8inch", Muons_8inch, 50, 5200, 1);
Muon_background_8inch->SetParNames("Norm_muons");

In [109]:
TF1* Gamma_background_8inch = new TF1("Gamma_background_8inch", Gammas_8inch, 50, 5200, 1);
Gamma_background_8inch->SetParNames("Norm_gammas");

In [110]:
TF1* SignalandBackground_8inch = new TF1("SignalandBackground_8inch", SignalPlusBackground_8inch, 50, 5000, 5);
SignalandBackground_8inch->SetParNames("Norm_muons", "Norm_gammas", "Norm_Neutr", "Mean_gauss", "Sigma_gauss");

## Fit

### DCHut

In [111]:
TH1D* h_DC_8inch = Put_data_in_histo("Measures@DCHut/2022-09-14_BS-A-06_RT_1733984.75_LV_1733461.01.dat", 1733984, "8inch at DChut");
h_DC_8inch->Rebin(4);
h_DC_8inch->Scale(1/4.);


*******************************************************
Measures@DCHut/2022-09-14_BS-A-06_RT_1733984.75_LV_1733461.01.dat


In [112]:
TH1D* hCal_DC_8inch = Calibrate_histo(h_DC_8inch, Cal_factor_8inch, Form("%s_keVee", h_DC_8inch->GetTitle()));

In [113]:
SignalandBackground_8inch->SetParameter(3, 3500);
SignalandBackground_8inch->SetParLimits(3, 3300, 3700);
SignalandBackground_8inch->SetParameter(2, 1);
SignalandBackground_8inch->SetParameter(4, 40*Cal_factor);

TFitResultPtr r_8_DC = hCal_DC_8inch->Fit(SignalandBackground_8inch, "SR0", "", 500, 6000);

TMatrixD CovMat_8_DC = r_8_DC->GetCovarianceMatrix();

//CovMat_8_DC.Print();

Double_t err_norm_NP_8_DC = sqrt(CovMat_8_DC(2,2));
Double_t norm_NP_8_DC = SignalandBackground_8inch->GetParameter(2);

Double_t err_norm_Bkg_8_DC = sqrt(CovMat_8_DC(0,0)+CovMat_8_DC(1,1)+2*CovMat_8_DC(0,1));
Double_t norm_Bckg_8_DC = SignalandBackground_8inch->GetParameter(0)+SignalandBackground_8inch->GetParameter(1);

Double_t Norm_mu_8_DC = SignalandBackground_8inch->GetParameter(0);
Double_t err_Norm_mu_8_DC = SignalandBackground_8inch->GetParError(0);

Sum_background_8inch->SetParameter(0, SignalandBackground_8inch->GetParameter(0));
Sum_background_8inch->SetParameter(1, SignalandBackground_8inch->GetParameter(1));

Muon_background_8inch->SetParameter(0, SignalandBackground_8inch->GetParameter(0));
Gamma_background_8inch->SetParameter(0, SignalandBackground_8inch->GetParameter(1));

Neutron_peak_Gaus->SetParameter(0, SignalandBackground_8inch->GetParameter(2));
Neutron_peak_Gaus->SetParameter(1, SignalandBackground_8inch->GetParameter(3));
Neutron_peak_Gaus->SetParameter(2, SignalandBackground_8inch->GetParameter(4));

Double_t N_ev_tot_8_DC = SignalandBackground_8inch->Integral(Emin, Emax);
Double_t N_ev_NP_8_DC = Neutron_peak_Gaus->Integral(Emin, Emax);
Double_t err_N_ev_NP_8_DC = (err_norm_NP_8_DC/norm_NP_8_DC)*Neutron_peak_Gaus->Integral(Emin, Emax);
Double_t N_ev_BKG_8_DC = Sum_background_8inch->Integral(Emin, Emax);
Double_t err_N_ev_BKG_8_DC = (err_norm_Bkg_8_DC/norm_Bckg_8_DC)*Sum_background_8inch->Integral(Emin, Emax);

Double_t err_N_ev_data_8_DC;
Double_t N_ev_data_8_DC = hCal_DC_8inch->IntegralAndError(hCal_DC_8inch->FindBin(Emin), hCal_DC_8inch->FindBin(Emax), err_N_ev_data_8_DC, "width");

Double_t err_N_ev_data_NP_8_DC = sqrt(err_N_ev_data_8_DC*err_N_ev_data_8_DC + err_N_ev_BKG_8_DC*err_N_ev_BKG_8_DC);
Double_t N_ev_data_NP_8_DC = N_ev_data_8_DC-N_ev_BKG_8_DC;

cout<<"\nChi2/ndf = "<<SignalandBackground_8inch->GetChisquare()<<"/"<<SignalandBackground_8inch->GetNDF()<<" = "<<SignalandBackground_8inch->GetChisquare()/SignalandBackground_8inch->GetNDF()<<endl;
cout<<"\nTotal N_ev in peak region = "<<N_ev_data_8_DC<<" ev/d +- "<<err_N_ev_data_8_DC<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from fit = "<<N_ev_NP_8_DC<<" ev/d +- "<<err_N_ev_NP_8_DC<<" ev/d (error from normalization error only!)"<<endl;
cout<<"N_ev in background = "<<N_ev_BKG_8_DC<<" ev/d +- "<<err_N_ev_BKG_8_DC<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from data - bckg = "<<N_ev_data_NP_8_DC<<" ev/d +- "<<err_N_ev_data_NP_8_DC<<" ev/d"<<endl;

SignalandBackground_8inch->FixParameter(4, SignalandBackground_8inch->GetParameter(4)); //Fix the sigma value of the neutron peak

 FCN=626.469 FROM MIGRAD    STATUS=CONVERGED     217 CALLS         218 TOTAL
                     EDM=1.12991e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   3.70257e-01   2.91399e-03   3.09888e-05   1.33103e-02
   2  Norm_gammas   1.25473e+00   1.03429e-02   1.13065e-04   1.91804e-02
   3  Norm_Neutr   1.48091e-01   5.42951e-03   5.01792e-05  -8.13681e-02
   4  Mean_gauss   3.66296e+03   9.73976e+00   9.99572e-04  -2.97005e-03
   5  Sigma_gauss   2.85250e+02   1.01429e+01   9.07673e-02  -5.36461e-05

Chi2/ndf = 626.469/110 = 5.69517

Total N_ev in peak region = 194.327 ev/d +- 3.11172 ev/d
N_ev in neutron peak from fit = 103.471 ev/d +- 3.79357 ev/d (error from normalization error only!)
N_ev in background = 83.1801 ev/d +- 0.481359 ev/d
N_ev in neutron peak from data - bckg = 111.147 ev/d +- 3.14873 ev/d


In [114]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hCal_DC_8inch->Draw("");
Sum_background_8inch->SetLineColor(kBlue);
Muon_background_8inch->SetLineColor(kGreen);
Gamma_background_8inch->SetLineColor(kRed);
SignalandBackground_8inch->SetLineColor(kBlack);
Muon_background_8inch->Draw("RSAME");
Gamma_background_8inch->Draw("RSAME");
Sum_background_8inch->Draw("RSAME");
SignalandBackground_8inch->Draw("Same");

TLegend* leg0 = new TLegend(0.6, 0.7, 0.89, 0.89);
leg0->AddEntry(Sum_background_8inch, "Background");
leg0->AddEntry(SignalandBackground_8inch, "Signal and Bckg");
leg0->AddEntry(Muon_background_8inch, "Muon Bckg");
leg0->AddEntry(Gamma_background_8inch, "Gamma Bckg");
leg0->Draw("SAME");

leg0->SetLineWidth(0);


TCanvas* C2 = new TCanvas("cRes_DC_8inch", "cRes_DC_8inch", 1.175*C->GetWw(), 0.6*C->GetWh());
C2->Draw();
TPad *p1 = new TPad("p1","p1",0.,0.02,0.795,1.);
p1->Draw();
p1->cd();
p1->SetRightMargin(0.03);
p1->SetBottomMargin(0.2);

histosRes_DC_8inch = Residuals_vec(hCal_DC_8inch, SignalandBackground_8inch, 500, 6000, true);
hRes_DC_8inch=histosRes_DC_8inch[0];
hRes_DC_8inch->GetYaxis()->SetTitle("Residuals [%]");
hRes_DC_8inch->GetYaxis()->SetTitleSize(1.9*hCal_DC_8inch->GetYaxis()->GetTitleSize());
hRes_DC_8inch->GetXaxis()->SetTitleSize(1.9*hCal_DC_8inch->GetXaxis()->GetTitleSize());
hRes_DC_8inch->GetYaxis()->SetLabelSize(1.9*hCal_DC_8inch->GetYaxis()->GetLabelSize());
hRes_DC_8inch->GetXaxis()->SetLabelSize(1.9*hCal_DC_8inch->GetXaxis()->GetLabelSize());
hRes_DC_8inch->Draw("");

h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10%");
leg->Draw("SAME");
leg->SetLineWidth(0);


C2->cd();
TPad *p2 = new TPad("p2","p2",0.795,0.02,1.,1.);
p2->Draw();
p2->cd();
p2->SetLeftMargin(0.15);
p2->SetBottomMargin(0.2);

hRedRes_DC_8inch=histosRes_DC_8inch[1];
hRedRes_DC_8inch->Draw("");
hRedRes_DC_8inch->GetXaxis()->SetTitle("Residuals [#sigma]");
hRedRes_DC_8inch->GetYaxis()->SetTitleSize(3.*hCal_DC_8inch->GetYaxis()->GetTitleSize());
hRedRes_DC_8inch->GetXaxis()->SetTitleSize(2.7*hCal_DC_8inch->GetXaxis()->GetTitleSize());
hRedRes_DC_8inch->GetXaxis()->SetTitleOffset(0.7);
hRedRes_DC_8inch->GetYaxis()->SetLabelSize(3.*hCal_DC_8inch->GetYaxis()->GetLabelSize());
hRedRes_DC_8inch->GetXaxis()->SetLabelSize(2.7*hCal_DC_8inch->GetXaxis()->GetLabelSize());
hRedRes_DC_8inch->GetXaxis()->SetNdivisions(5);

The low energy part is less well fitted: the gamma background chosen is limited + neutron contribution? At high energy, the background seems a bit underestimated: problem of model or only stat. effect ?

### VNS

In [115]:
TH1D* h_VNS_8inch_1 = Put_data_in_histo("Measures@VNS/2022-05-10_BS-A-06_RT_1133460.81_LV_1133048.44.dat", 1133460.81, "8inch at VNS - 1");
h_VNS_8inch_1->Rebin(4);
h_VNS_8inch_1->Scale(1/4.);

TH1D* h_VNS_8inch_2 = Put_data_in_histo("Measures@VNS/2022-05-25_BS-A-06_RT_1268564.89_LV_1268171.79.dat", 1268564.89, "8inch at VNS - 2");
h_VNS_8inch_2->Rebin(4);
h_VNS_8inch_2->Scale(1/4.);

TH1D* h_VNS_8inch_3 = Put_data_in_histo("Measures@VNS/2022-06-23_BS-A-06_RT_1374109.40_LV_1373731.67.dat", 1374109.40, "8inch at VNS - 3");
h_VNS_8inch_3->Rebin(4);
h_VNS_8inch_3->Scale(1/4.);

TH1D* h_VNS_8inch_4 = Put_data_in_histo("Measures@VNS/2022-07-27_BS-A-06_RT_674093.29_LV_673979.29.dat", 674093.29, "8inch at VNS - 4");
h_VNS_8inch_4->Rebin(4);
h_VNS_8inch_4->Scale(1/4.);


*******************************************************
Measures@VNS/2022-05-10_BS-A-06_RT_1133460.81_LV_1133048.44.dat

*******************************************************
Measures@VNS/2022-05-25_BS-A-06_RT_1268564.89_LV_1268171.79.dat

*******************************************************
Measures@VNS/2022-06-23_BS-A-06_RT_1374109.40_LV_1373731.67.dat

*******************************************************
Measures@VNS/2022-07-27_BS-A-06_RT_674093.29_LV_673979.29.dat


In [116]:
TH1D* h_VNS_8inch_sum = (TH1D*) h_VNS_8inch_1->Clone();
h_VNS_8inch_sum->Add(h_VNS_8inch_sum, h_VNS_8inch_2, 1/4., 1/4.); 
h_VNS_8inch_sum->Add(h_VNS_8inch_sum, h_VNS_8inch_3, 1, 1/4.);
h_VNS_8inch_sum->Add(h_VNS_8inch_sum, h_VNS_8inch_4, 1, 1/4.);
h_VNS_8inch_sum->SetTitle("8inch at VNS - sum");

In [117]:
TH1D* hCal_VNS_8inch = Calibrate_histo(h_VNS_8inch_sum, Cal_factor_8inch, Form("%s_keVee", h_VNS_8inch_sum->GetTitle()));

In [118]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hCal_VNS_8inch->Draw();
hCal_VNS_9inch->Draw("SAME");

In [119]:
TFitResultPtr r_8_VNS = hCal_VNS_8inch->Fit(SignalandBackground_8inch, "SR0", "", 1100, 6000);
r_8_VNS = hCal_VNS_8inch->Fit(SignalandBackground_8inch, "SR0", "", 1100, 6000);

TMatrixD CovMat_8_VNS = r_8_VNS->GetCovarianceMatrix();

//CovMat_8_VNS.Print();

Double_t err_norm_NP_8_VNS = sqrt(CovMat_8_VNS(2,2));
Double_t norm_NP_8_VNS = SignalandBackground_8inch->GetParameter(2);

Double_t err_norm_Bkg_8_VNS = sqrt(CovMat_8_VNS(0,0)+CovMat_8_VNS(1,1)+2*CovMat_8_VNS(0,1));
Double_t norm_Bckg_8_VNS = SignalandBackground_8inch->GetParameter(0)+SignalandBackground_8inch->GetParameter(1);

Double_t Norm_mu_8_VNS = SignalandBackground_8inch->GetParameter(0);
Double_t err_Norm_mu_8_VNS = SignalandBackground_8inch->GetParError(0);

Sum_background_8inch->SetParameter(0, Norm_mu_8_VNS);
Sum_background_8inch->SetParameter(1, SignalandBackground_8inch->GetParameter(1));

Muon_background_8inch->SetParameter(0, SignalandBackground_8inch->GetParameter(0));
Gamma_background_8inch->SetParameter(0, SignalandBackground_8inch->GetParameter(1));

Neutron_peak_Gaus->SetParameter(0, SignalandBackground_8inch->GetParameter(2));
Neutron_peak_Gaus->SetParameter(1, SignalandBackground_8inch->GetParameter(3));
Neutron_peak_Gaus->SetParameter(2, SignalandBackground_8inch->GetParameter(4));

Double_t N_ev_tot_8_VNS = SignalandBackground_8inch->Integral(Emin, Emax);
Double_t N_ev_NP_8_VNS = Neutron_peak_Gaus->Integral(Emin, Emax);
Double_t err_N_ev_NP_8_VNS = (err_norm_NP_8_VNS/norm_NP_8_VNS)*Neutron_peak_Gaus->Integral(Emin, Emax);
Double_t N_ev_BKG_8_VNS = Sum_background_8inch->Integral(Emin, Emax);
Double_t err_N_ev_BKG_8_VNS = (err_norm_Bkg_8_VNS/norm_Bckg_8_VNS)*Sum_background_8inch->Integral(Emin, Emax);

Double_t err_N_ev_data_8_VNS;
Double_t N_ev_data_8_VNS = hCal_VNS_8inch->IntegralAndError(hCal_VNS_8inch->FindBin(Emin), hCal_VNS_8inch->FindBin(Emax), err_N_ev_data_8_VNS, "width");

Double_t err_N_ev_data_NP_8_VNS = sqrt(err_N_ev_data_8_VNS*err_N_ev_data_8_VNS + err_N_ev_BKG_8_VNS*err_N_ev_BKG_8_VNS);
Double_t N_ev_data_NP_8_VNS = N_ev_data_8_VNS-N_ev_BKG_8_VNS;

cout<<"\nChi2/ndf = "<<SignalandBackground_8inch->GetChisquare()<<"/"<<SignalandBackground_8inch->GetNDF()<<" = "<<SignalandBackground_8inch->GetChisquare()/SignalandBackground_8inch->GetNDF()<<endl;
cout<<"\nTotal N_ev in peak region = "<<N_ev_data_8_VNS<<" ev/d +- "<<err_N_ev_data_8_VNS<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from fit = "<<N_ev_NP_8_VNS<<" ev/d +- "<<err_N_ev_NP_8_VNS<<" ev/d (error from normalization error only!)"<<endl;
cout<<"N_ev in background = "<<N_ev_BKG_8_VNS<<" ev/d +- "<<err_N_ev_BKG_8_VNS<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from data - bckg = "<<N_ev_data_NP_8_VNS<<" ev/d +- "<<err_N_ev_data_NP_8_VNS<<" ev/d"<<endl;

 FCN=225.803 FROM MIGRAD    STATUS=CONVERGED     110 CALLS         111 TOTAL
                     EDM=4.00548e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   2.14502e-01   2.22589e-03   1.05612e-05  -1.85016e-06
   2  Norm_gammas   1.98384e+00   3.57219e-02   1.79046e-04  -1.17507e-06
   3  Norm_Neutr   1.19981e-04   1.61763e-03   1.06944e-05  -1.25240e-05
   4  Mean_gauss   3.30000e+03   2.84399e+02   1.44477e-02  -6.32362e-04
   5  Sigma_gauss   2.85250e+02     fixed    
 FCN=201.343 FROM MIGRAD    STATUS=CONVERGED     113 CALLS         114 TOTAL
                     EDM=1.41325e-11    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   2.11023e-01   2.12789e-03   9.97544e-06 

In [120]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hCal_VNS_8inch->Draw("");
Sum_background_8inch->SetLineColor(kBlue);
Sum_background_8inch->Draw("RSAME");
Muon_background_8inch->SetLineColor(kGreen);
Gamma_background_8inch->SetLineColor(kRed);
SignalandBackground_8inch->SetLineColor(kBlack);
Muon_background_8inch->Draw("RSAME");
Gamma_background_8inch->Draw("RSAME");
SignalandBackground_8inch->Draw("RSAME");

TLegend* leg0 = new TLegend(0.6, 0.7, 0.89, 0.89);
leg0->AddEntry(Sum_background_8inch, "Background");
leg0->AddEntry(SignalandBackground_8inch, "Signal and Bckg");
leg0->AddEntry(Muon_background_8inch, "Muon Bckg");
leg0->AddEntry(Gamma_background_8inch, "Gamma Bckg");
leg0->SetLineWidth(0);
leg0->Draw("SAME");

TCanvas* C2 = new TCanvas("cRes_VNS_8inch", "cRes_VNS_8inch", 1.175*C->GetWw(), 0.6*C->GetWh());
C2->Draw();
TPad *p1 = new TPad("p1","p1",0.,0.02,0.795,1.);
p1->Draw();
p1->cd();
p1->SetRightMargin(0.03);
p1->SetBottomMargin(0.2);

histosRes_VNS_8inch = Residuals_vec(hCal_VNS_8inch, SignalandBackground_8inch, 1100, 6000, true);
hRes_VNS_8inch=histosRes_VNS_8inch[0];
hRes_VNS_8inch->GetYaxis()->SetTitle("Residuals [%]");
hRes_VNS_8inch->GetYaxis()->SetTitleSize(1.9*hCal_VNS_8inch->GetYaxis()->GetTitleSize());
hRes_VNS_8inch->GetXaxis()->SetTitleSize(1.9*hCal_VNS_8inch->GetXaxis()->GetTitleSize());
hRes_VNS_8inch->GetYaxis()->SetLabelSize(1.9*hCal_VNS_8inch->GetYaxis()->GetLabelSize());
hRes_VNS_8inch->GetXaxis()->SetLabelSize(1.9*hCal_VNS_8inch->GetXaxis()->GetLabelSize());
hRes_VNS_8inch->Draw("");

h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10%");
leg->Draw("SAME");
leg->SetLineWidth(0);


C2->cd();
TPad *p2 = new TPad("p2","p2",0.795,0.02,1.,1.);
p2->Draw();
p2->cd();
p2->SetLeftMargin(0.15);
p2->SetBottomMargin(0.2);

hRedRes_VNS_8inch=histosRes_VNS_8inch[1];
hRedRes_VNS_8inch->Draw("");
hRedRes_VNS_8inch->GetXaxis()->SetTitle("Residuals [#sigma]");
hRedRes_VNS_8inch->GetYaxis()->SetTitleSize(3.*hCal_VNS_8inch->GetYaxis()->GetTitleSize());
hRedRes_VNS_8inch->GetXaxis()->SetTitleSize(2.7*hCal_VNS_8inch->GetXaxis()->GetTitleSize());
hRedRes_VNS_8inch->GetXaxis()->SetTitleOffset(0.7);
hRedRes_VNS_8inch->GetYaxis()->SetLabelSize(3.*hCal_VNS_8inch->GetYaxis()->GetLabelSize());
hRedRes_VNS_8inch->GetXaxis()->SetLabelSize(2.7*hCal_VNS_8inch->GetXaxis()->GetLabelSize());
hRedRes_VNS_8inch->GetXaxis()->SetNdivisions(5);

# Attenuation from VNS


The >10 MeV neutron contribution is expected to be extracted from the difference between the number of events with the 9inch and the 8inch spheres. 

## First "naive" calculation of the attenuation

In [121]:
cout<<"------------------------------ VNS -------------------------------"<<endl;
cout<<" 9inch: "<< N_ev_data_NP_VNS << " +- " << err_N_ev_data_NP_VNS<<" (stat.) "<<endl;
cout<<" 8inch: "<< N_ev_data_NP_8_VNS << " +- " << err_N_ev_data_NP_8_VNS<<" (stat.) "<<endl;

cout<<"\n------------------------ Surface (DCHut) -----------------------"<<endl;
cout<<" 9inch: "<< N_ev_data_NP_DC << " +- " << err_N_ev_data_NP_DC<<" (stat.) "<<endl;
cout<<" 8inch: "<< N_ev_data_NP_8_DC << " +- " << err_N_ev_data_NP_8_DC<<" (stat.) "<<endl;

------------------------------ VNS -------------------------------
 9inch: 7.74908 +- 1.60181 (stat.) 
 8inch: 6.92556 +- 1.29609 (stat.) 

------------------------ Surface (DCHut) -----------------------
 9inch: 145.958 +- 2.71801 (stat.) 
 8inch: 111.147 +- 3.14873 (stat.) 


In [122]:
FastNeutrons_Surface = N_ev_data_NP_DC-N_ev_data_NP_8_DC;
err_FastNeutrons_Surface = sqrt(err_N_ev_data_NP_DC*err_N_ev_data_NP_DC+err_N_ev_data_NP_8_DC*err_N_ev_data_NP_8_DC);

FastNeutrons_VNS = N_ev_data_NP_VNS-N_ev_data_NP_8_VNS;
err_FastNeutrons_VNS = sqrt(err_N_ev_data_NP_VNS*err_N_ev_data_NP_VNS+err_N_ev_data_NP_8_VNS*err_N_ev_data_NP_8_VNS);

cout<< ">10MeV Neutron contribution"<<endl;
cout<< "----------------------------"<<endl;
cout<<"Surface: "<<FastNeutrons_Surface<<" +- "<<err_FastNeutrons_Surface<<" (stat. only) ev/d"<<endl;
cout<<"VNS: "<<FastNeutrons_VNS<<" +- "<<err_FastNeutrons_VNS<<" (stat. only) ev/d"<<endl;

>10MeV Neutron contribution
----------------------------
Surface: 34.8113 +- 4.15958 (stat. only) ev/d
VNS: 0.823524 +- 2.0605 (stat. only) ev/d


In [123]:
Ratio = FastNeutrons_Surface/FastNeutrons_VNS;
err_Ratio = Ratio*sqrt((err_FastNeutrons_VNS/FastNeutrons_VNS)*(err_FastNeutrons_VNS/FastNeutrons_VNS)+(err_FastNeutrons_Surface/FastNeutrons_Surface)*(err_FastNeutrons_Surface/FastNeutrons_Surface));

cout<<"Ratio = "<<Ratio<<" +- "<<err_Ratio<< " (stat. only)" << endl; 

Ratio = 42.2712 +- 105.885 (stat. only)


<b>Aside</b>: Let's check the consistency of the attenuation observed for muons

In [124]:
cout<<"Muons attenuation in 8inch = "<<Norm_mu_8_DC/Norm_mu_8_VNS<<" +- "<<(Norm_mu_8_DC/Norm_mu_8_VNS)*sqrt((err_Norm_mu_8_DC/Norm_mu_8_DC)*(err_Norm_mu_8_DC/Norm_mu_8_DC)+(err_Norm_mu_8_VNS/Norm_mu_8_VNS)*(err_Norm_mu_8_VNS/Norm_mu_8_VNS))<<endl;
cout<<"Muons attenuation in 9inch = "<<Norm_mu_9_DC/Norm_mu_9_VNS<<" +- "<<(Norm_mu_9_DC/Norm_mu_9_VNS)*sqrt((err_Norm_mu_9_DC/Norm_mu_9_DC)*(err_Norm_mu_9_DC/Norm_mu_9_DC)+(err_Norm_mu_9_VNS/Norm_mu_9_VNS)*(err_Norm_mu_9_VNS/Norm_mu_9_VNS))<<endl;

Muons attenuation in 8inch = 1.75458 +- 0.0224436
Muons attenuation in 9inch = 1.96283 +- 0.0239912


The attenuation value is close to the one expected (1.4) but they are not compatible with each other at 1 sigma. This can be due to simplificity of the neutron contribution in the DC data? Gamma/Muon backgrounds not correctly modelled? 

## Estimate of the attenuation from a Toy MonteCarlo

### Considering stat. errors only

In [125]:
TF1* Gaus_ev_DC = new TF1("Gauss_ev_DC", "TMath::Gaus(x, [0], [1], true)", 0, FastNeutrons_Surface+5*err_FastNeutrons_Surface);
Gaus_ev_DC->FixParameter(0, FastNeutrons_Surface);
Gaus_ev_DC->FixParameter(1, err_FastNeutrons_Surface);

TF1* Gaus_ev_VNS = new TF1("Gauss_ev_VNS", "TMath::Gaus(x, [0], [1], true)", 0, FastNeutrons_VNS+5*err_FastNeutrons_VNS);
Gaus_ev_VNS->FixParameter(0, FastNeutrons_VNS);
Gaus_ev_VNS->FixParameter(1, err_FastNeutrons_VNS);

In [126]:
TH1D* hRatio = new TH1D("Attenuation factor from Toy MC", "Attenuation factor from Toy MC", 10000, 0, 500);
Double_t Ev_out, Ev_VNS;   
for (int i=0; i<100000; i++){
    Ev_out = Gaus_ev_DC->GetRandom();
    Ev_VNS = Gaus_ev_VNS->GetRandom();
    if ((Ev_VNS>0)&&(Ev_out>0)) {hRatio->Fill(Ev_out/Ev_VNS);}
}

hRatio->GetXaxis()->SetRangeUser(0, 20);
hRatio->GetXaxis()->SetTitle("R^{Out}/R_{VNS}");
hRatio->GetYaxis()->SetTitle("Probability");
hRatio->Scale(1./hRatio->Integral());

In [127]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hRatio->Draw("");

In [128]:
Double_t Rmin=0;
Double_t Pas=0.02;
Double_t int_below_min=0;
while (int_below_min<0.05){
    Rmin+= Pas;
    int_below_min = hRatio->Integral(0, hRatio->FindBin(Rmin));
}
Rmin -= Pas;
int_below_min = hRatio->Integral(0, hRatio->FindBin(Rmin));

cout<<"Attenuation factor > "<< Rmin<<" at "<<(1-int_below_min)*100 << " % confidence level"<<endl;

Attenuation factor > 6.4 at 95.2225 % confidence level


### With previous fits (linear and exponential)

#### Linear

In [129]:
TF1* Gaus_ev_DC_lin = new TF1("Gaus_ev_DC_lin", "TMath::Gaus(x, [0], [1], true)", 0, 22+5*6.2);
Gaus_ev_DC_lin->FixParameter(0, 21.7);
Gaus_ev_DC_lin->FixParameter(1, 6.2);

TF1* Gaus_ev_VNS_lin = new TF1("Gaus_ev_VNS_lin", "TMath::Gaus(x, [0], [1], true)", 0, 4.8+5*7);
Gaus_ev_VNS_lin->FixParameter(0, 4.8);
Gaus_ev_VNS_lin->FixParameter(1, 6.9);

In [130]:
TH1D* hRatio_lin = new TH1D("Attenuation factor from Toy MC with linear fit", "Attenuation factor from Toy MC with linear fit", 10000, 0, 500);
Double_t Ev_out, Ev_VNS;   
for (int i=0; i<100000; i++){
    Ev_out = Gaus_ev_DC_lin->GetRandom();
    Ev_VNS = Gaus_ev_VNS_lin->GetRandom();
    if ((Ev_VNS>0)&&(Ev_out>0)) {hRatio_lin->Fill(Ev_out/Ev_VNS);}
}

hRatio_lin->GetXaxis()->SetRangeUser(0, 20);
hRatio_lin->GetXaxis()->SetTitle("R^{Out}/R_{VNS}");
hRatio_lin->GetYaxis()->SetTitle("Probability");
hRatio_lin->Scale(1./hRatio_lin->Integral());

In [131]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hRatio_lin->Draw("");

In [132]:
Double_t Rmin=0;
Double_t Pas=0.02;
Double_t int_below_min=0;
while (int_below_min<0.05){
    Rmin+= Pas;
    int_below_min = hRatio_lin->Integral(0, hRatio_lin->FindBin(Rmin));
}
Rmin -= Pas;
int_below_min = hRatio_lin->Integral(0, hRatio_lin->FindBin(Rmin));

cout<<"Attenuation factor > "<< Rmin<<" at "<<(1-int_below_min)*100 << " % confidence level"<<endl;

Attenuation factor > 0.98 at 95.1915 % confidence level


#### Exponential fit

In [133]:
TF1* Gaus_ev_DC_expo = new TF1("Gaus_ev_DC_expo", "TMath::Gaus(x, [0], [1], true)", 0, 39+5*9.2);
Gaus_ev_DC_expo->FixParameter(0, 39);
Gaus_ev_DC_expo->FixParameter(1, 9.2);

TF1* Gaus_ev_VNS_expo = new TF1("Gaus_ev_VNS_lin", "TMath::Gaus(x, [0], [1], true)", 0, 7.5+5*6.9);
Gaus_ev_VNS_expo->FixParameter(0, 7.5);
Gaus_ev_VNS_expo->FixParameter(1, 6.9);

In [134]:
TH1D* hRatio_expo = new TH1D("Attenuation factor from Toy MC with exponential fit", "Attenuation factor from Toy MC with exponential fit", 10000, 0, 500);
Double_t Ev_out, Ev_VNS;   
for (int i=0; i<100000; i++){
    Ev_out = Gaus_ev_DC_expo->GetRandom();
    Ev_VNS = Gaus_ev_VNS_expo->GetRandom();
    if ((Ev_VNS>0)&&(Ev_out>0)) {hRatio_expo->Fill(Ev_out/Ev_VNS);}
}

hRatio_expo->GetXaxis()->SetRangeUser(0, 20);
hRatio_expo->GetXaxis()->SetTitle("R^{Out}/R_{VNS}");
hRatio_expo->GetYaxis()->SetTitle("Probability");
hRatio_expo->Scale(1./hRatio_expo->Integral());

In [135]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hRatio_expo->Draw("");

In [136]:
Double_t Rmin=0;
Double_t Pas=0.02;
Double_t int_below_min=0;
while (int_below_min<0.05){
    Rmin+= Pas;
    int_below_min = hRatio_expo->Integral(0, hRatio_expo->FindBin(Rmin));
}
Rmin -= Pas;
int_below_min = hRatio_expo->Integral(0, hRatio_expo->FindBin(Rmin));

cout<<"Attenuation factor > "<< Rmin<<" at "<<(1-int_below_min)*100 << " % confidence level"<<endl;

Attenuation factor > 1.68 at 95.0669 % confidence level


# Other fitting methods

## Local linear background

In [137]:
TF1* Model_linear = new TF1("Model_linear", "gaus(0)+pol1(3)", 3000, 4700);

In [138]:
TF1* Linear_bckg = new TF1("Linear_bckg", "pol1", 3000, 4700);

### 9inch

In [139]:
Int_start = 3000;
Int_stop = 4500;

Model_linear->SetParameter(1, 3500);
if (Model_linear->GetParameter(2)==0) Model_linear->SetParameter(2, Resol_NP*3500);

TFitResultPtr r = hCal_DC_9inch->Fit(Model_linear, "S0", "", 3000, 5100);

TMatrixD CovMat_9_lin_DC = r->GetCovarianceMatrix();

//CovMat_DC.Print();

Double_t err_norm_NP_DC_lin = sqrt(CovMat_9_lin_DC(0,0));
Double_t norm_NP_DC_lin = Model_linear->GetParameter(0);

Linear_bckg->SetParameter(0, Model_linear->GetParameter(3));
Linear_bckg->SetParameter(1, Model_linear->GetParameter(4));

Neutron_signal_9inch->SetParameter(0, Model_linear->GetParameter(0));
Neutron_signal_9inch->SetParameter(1, Model_linear->GetParameter(1));
Neutron_signal_9inch->SetParameter(2, Model_linear->GetParameter(2));

Double_t N_ev_tot_DC_lin = Model_linear->Integral(Int_start, Int_stop);
Double_t N_ev_NP_DC_lin = Neutron_signal_9inch->Integral(Int_start, Int_stop);
Double_t err_N_ev_NP_DC_lin = (err_norm_NP_DC_lin/norm_NP_DC_lin)*Neutron_signal_9inch->Integral(Int_start, Int_stop);
Double_t N_ev_BKG_DC_lin = Linear_bckg->Integral(Int_start, Int_stop);
Double_t err_N_ev_BKG_DC_lin = sqrt((Int_stop-Int_start)*(Int_stop-Int_start)*CovMat_9_lin_DC(3,3)+(Int_stop-Int_start)*(Int_stop*Int_stop-Int_start*Int_start)*CovMat_9_lin_DC(3, 4)+(Int_stop*Int_stop-Int_start*Int_start)*(Int_stop*Int_stop-Int_start*Int_start)*CovMat_9_lin_DC(4,4)/4);

Double_t err_N_ev_data_DC_lin;
Double_t N_ev_data_DC_lin = hCal_DC_9inch->IntegralAndError(hCal_DC_9inch->FindBin(Int_start), hCal_DC_9inch->FindBin(Int_stop), err_N_ev_data_DC_lin, "width");

Double_t err_N_ev_data_NP_DC_lin = sqrt(err_N_ev_data_DC_lin*err_N_ev_data_DC_lin + err_N_ev_BKG_DC_lin*err_N_ev_BKG_DC_lin);
Double_t N_ev_data_NP_DC_lin = N_ev_data_DC_lin-N_ev_BKG_DC_lin;

cout<<"\nChi2/ndf = "<<Model_linear->GetChisquare()<<"/"<<Model_linear->GetNDF()<<" = "<<Model_linear->GetChisquare()/Model_linear->GetNDF()<<endl;
cout<<"\nTotal N_ev in peak region = "<<N_ev_data_DC_lin<<" ev/d +- "<<err_N_ev_data_DC_lin<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from fit = "<<N_ev_NP_DC_lin<<" ev/d +- "<<err_N_ev_NP_DC_lin<<" ev/d "<<endl;
cout<<"N_ev in background = "<<N_ev_BKG_DC_lin<<" ev/d +- "<<err_N_ev_BKG_DC_lin<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from data - bckg = "<<N_ev_data_NP_DC_lin<<" ev/d +- "<<err_N_ev_data_NP_DC_lin<<" ev/d"<<endl;

Model_linear->FixParameter(2, Model_linear->GetParameter(2)); //Fix the sigma value of the neutron peak  

 FCN=100.981 FROM MIGRAD    STATUS=CONVERGED     437 CALLS         438 TOTAL
                     EDM=1.3714e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  p0           1.78345e-01   5.91280e-03   1.79543e-05  -9.68555e-02
   2  p1           3.65242e+03   1.06937e+01   3.42400e-02  -1.47161e-05
   3  p2           2.76051e+02   1.34460e+01   2.46614e-02  -9.44618e-05
   4  p3           2.66061e-01   2.27705e-02   4.52736e-06  -4.70172e-01
   5  p4          -4.95240e-05   4.73516e-06   9.97773e-10  -1.98830e+03

Chi2/ndf = 100.981/45 = 2.24402

Total N_ev in peak region = 247.455 ev/d +- 2.68769 ev/d
N_ev in neutron peak from fit = 64.1907 ev/d +- 2.12816 ev/d 
N_ev in background = 120.519 ev/d +- 34.633 ev/d
N_ev in neutron peak from data - bckg = 126.937 ev/d +- 34.7371 ev/d


In [140]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hCal_DC_9inch->Draw("");
hCal_DC_9inch->GetYaxis()->SetRangeUser(1e-4, 10);
Linear_bckg->SetLineColor(kBlue);
Linear_bckg->Draw("RSAME");
Model_linear->Draw("RSAME");

TCanvas* C2 = new TCanvas("cRes_DC_9inch_lin", "cRes_DC_9inch_lin", C->GetWw(), 0.6*C->GetWh());
C2->Draw();
gPad->SetMargin(0.1,0.1,0.2,0.1);

hRes_DC_9inch_lin=Residuals(hCal_DC_9inch, Model_linear, 3000, 4700, true);
hRes_DC_9inch_lin->GetYaxis()->SetTitle("Residuals [%]");
hRes_DC_9inch_lin->GetYaxis()->SetTitleSize(2*hCal_DC_9inch->GetYaxis()->GetTitleSize());
hRes_DC_9inch_lin->GetXaxis()->SetTitleSize(2*hCal_DC_9inch->GetXaxis()->GetTitleSize());
hRes_DC_9inch_lin->GetYaxis()->SetLabelSize(2*hCal_DC_9inch->GetYaxis()->GetLabelSize());
hRes_DC_9inch_lin->GetXaxis()->SetLabelSize(2*hCal_DC_9inch->GetXaxis()->GetLabelSize());
hRes_DC_9inch_lin->Draw("");

h_10pc->SetLineColorAlpha(kOrange+1, 0.2);
h_10pc->SetMarkerColorAlpha(kOrange+1, 0.2);
h_10pc->SetFillColorAlpha(kOrange+1, 0.2);
h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10%");
leg->Draw("SAME");
leg->SetLineWidth(0);

In [141]:
Int_start = 3000;
Int_stop = 4500;

Model_linear->SetParLimits(0, 0, 10);

TFitResultPtr r = hCal_VNS_9inch->Fit(Model_linear, "S0", "", 3000, 4700);

TMatrixD CovMat_9_lin_VNS = r->GetCovarianceMatrix();

//CovMat_DC.Print();

Double_t err_norm_NP_VNS_lin = sqrt(CovMat_9_lin_VNS(0,0));
Double_t norm_NP_VNS_lin = Model_linear->GetParameter(0);

Linear_bckg->SetParameter(0, Model_linear->GetParameter(3));
Linear_bckg->SetParameter(1, Model_linear->GetParameter(4));

Neutron_signal_9inch->SetParameter(0, Model_linear->GetParameter(0));
Neutron_signal_9inch->SetParameter(1, Model_linear->GetParameter(1));
Neutron_signal_9inch->SetParameter(2, Model_linear->GetParameter(2));

Double_t N_ev_tot_VNS_lin = Model_linear->Integral(Int_start, Int_stop);
Double_t N_ev_NP_VNS_lin = Neutron_signal_9inch->Integral(Int_start, Int_stop);
Double_t err_N_ev_NP_VNS_lin = (err_norm_NP_VNS_lin/norm_NP_VNS_lin)*Neutron_signal_9inch->Integral(Int_start, Int_stop);
Double_t N_ev_BKG_VNS_lin = Linear_bckg->Integral(Int_start, Int_stop);
Double_t err_N_ev_BKG_VNS_lin = sqrt((Int_stop-Int_start)*(Int_stop-Int_start)*CovMat_9_lin_VNS(3,3)+(Int_stop-Int_start)*(Int_stop*Int_stop-Int_start*Int_start)*CovMat_9_lin_VNS(3, 4)+(Int_stop*Int_stop-Int_start*Int_start)*(Int_stop*Int_stop-Int_start*Int_start)*CovMat_9_lin_VNS(4,4)/4);

Double_t err_N_ev_data_VNS_lin;
Double_t N_ev_data_VNS_lin = hCal_VNS_9inch->IntegralAndError(hCal_VNS_9inch->FindBin(Int_start), hCal_VNS_9inch->FindBin(Int_stop), err_N_ev_data_VNS_lin, "width");

Double_t err_N_ev_data_NP_VNS_lin = sqrt(err_N_ev_data_VNS_lin*err_N_ev_data_VNS_lin + err_N_ev_BKG_VNS_lin*err_N_ev_BKG_VNS_lin);
Double_t N_ev_data_NP_VNS_lin = N_ev_data_VNS_lin-N_ev_BKG_VNS_lin;

cout<<"\nChi2/ndf = "<<Model_linear->GetChisquare()<<"/"<<Model_linear->GetNDF()<<" = "<<Model_linear->GetChisquare()/Model_linear->GetNDF()<<endl;
cout<<"\nTotal N_ev in peak region = "<<N_ev_data_VNS_lin<<" ev/d +- "<<err_N_ev_data_VNS_lin<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from fit = "<<N_ev_NP_VNS_lin<<" ev/d +- "<<err_N_ev_NP_VNS_lin<<" ev/d "<<endl;
cout<<"N_ev in background = "<<N_ev_BKG_VNS_lin<<" ev/d +- "<<err_N_ev_BKG_VNS_lin<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from data - bckg = "<<N_ev_data_NP_VNS_lin<<" ev/d +- "<<err_N_ev_data_NP_VNS_lin<<" ev/d"<<endl;

 FCN=35.9189 FROM MIGRAD    STATUS=CONVERGED     274 CALLS         275 TOTAL
                     EDM=4.04631e-09    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  p0           1.04897e-02   3.11961e-03   1.31894e-05   1.78792e-02
   2  p1           3.48511e+03   5.60059e+01   1.51844e-01  -7.00541e-08
   3  p2           2.76051e+02     fixed    
   4  p3           1.37451e-01   9.37919e-03   1.60292e-06  -1.56865e-02
   5  p4          -2.78422e-05   2.13789e-06   3.84062e-10   6.21994e-01

Chi2/ndf = 35.9189/36 = 0.997746

Total N_ev in peak region = 58.1317 ev/d +- 1.10064 ev/d
N_ev in neutron peak from fit = 3.66325 ev/d +- 1.08946 ev/d 
N_ev in background = 49.5638 ev/d +- 14.2838 ev/d
N_ev in neutron peak from data - bckg = 8.56788 ev/d +- 14.3261 ev/d


In [142]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hCal_VNS_9inch->Draw("");
hCal_VNS_9inch->GetYaxis()->SetRangeUser(1e-4, 10);
Linear_bckg->SetLineColor(kBlue);
Linear_bckg->Draw("RSAME");
Model_linear->Draw("RSAME");

TCanvas* C2 = new TCanvas("cRes_VNS_9inch_lin", "cRes_VNS_9inch_lin", C->GetWw(), 0.6*C->GetWh());
C2->Draw();
gPad->SetMargin(0.1,0.1,0.2,0.1);

hRes_VNS_9inch_lin=Residuals(hCal_VNS_9inch, Model_linear, 2900, 4700, true);
hRes_VNS_9inch_lin->GetYaxis()->SetTitle("Residuals [%]");
hRes_VNS_9inch_lin->GetYaxis()->SetTitleSize(2*hCal_VNS_9inch->GetYaxis()->GetTitleSize());
hRes_VNS_9inch_lin->GetXaxis()->SetTitleSize(2*hCal_VNS_9inch->GetXaxis()->GetTitleSize());
hRes_VNS_9inch_lin->GetYaxis()->SetLabelSize(2*hCal_VNS_9inch->GetYaxis()->GetLabelSize());
hRes_VNS_9inch_lin->GetXaxis()->SetLabelSize(2*hCal_VNS_9inch->GetXaxis()->GetLabelSize());
hRes_VNS_9inch_lin->Draw("");

h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10 %");
leg->Draw("SAME");
leg->SetLineWidth(0);

### 8inch

In [143]:
Int_start = 3000;
Int_stop = 4500;

Model_linear->SetParameter(1, 3500);
if (Model_linear->GetParameter(2)==0) Model_linear->SetParameter(2, Resol_NP*3500);

TFitResultPtr r = hCal_DC_8inch->Fit(Model_linear, "S0", "", 2800, 5100);

TMatrixD CovMat_8_lin_DC = r->GetCovarianceMatrix();

//CovMat_DC.Print();

Double_t err_norm_8_NP_DC_lin = sqrt(CovMat_8_lin_DC(0,0));
Double_t norm_8_NP_DC_lin = Model_linear->GetParameter(0);

Linear_bckg->SetParameter(0, Model_linear->GetParameter(3));
Linear_bckg->SetParameter(1, Model_linear->GetParameter(4));

Neutron_peak_Gaus->SetParameter(0, Model_linear->GetParameter(0));
Neutron_peak_Gaus->SetParameter(1, Model_linear->GetParameter(1));
Neutron_peak_Gaus->SetParameter(2, Model_linear->GetParameter(2));

Double_t N_ev_tot_8_DC_lin = Model_linear->Integral(Int_start, Int_stop);
Double_t N_ev_NP_8_DC_lin = Neutron_peak_Gaus->Integral(Int_start, Int_stop);
Double_t err_N_ev_NP_8_DC_lin = (err_norm_8_NP_DC_lin/norm_8_NP_DC_lin)*Neutron_peak_Gaus->Integral(Int_start, Int_stop);
Double_t N_ev_BKG_8_DC_lin = Linear_bckg->Integral(Int_start, Int_stop);
Double_t err_N_ev_BKG_8_DC_lin = sqrt((Int_stop-Int_start)*(Int_stop-Int_start)*CovMat_8_lin_DC(3,3)+(Int_stop-Int_start)*(Int_stop*Int_stop-Int_start*Int_start)*CovMat_8_lin_DC(3, 4)+(Int_stop*Int_stop-Int_start*Int_start)*(Int_stop*Int_stop-Int_start*Int_start)*CovMat_8_lin_DC(4,4)/4);

Double_t err_N_ev_data_8_DC_lin;
Double_t N_ev_data_8_DC_lin = hCal_DC_8inch->IntegralAndError(hCal_DC_8inch->FindBin(Int_start), hCal_DC_8inch->FindBin(Int_stop), err_N_ev_data_8_DC_lin, "width");

Double_t err_N_ev_data_8_NP_DC_lin = sqrt(err_N_ev_data_8_DC_lin*err_N_ev_data_8_DC_lin + err_N_ev_BKG_8_DC_lin*err_N_ev_BKG_8_DC_lin);
Double_t N_ev_data_NP_8_DC_lin = N_ev_data_8_DC_lin-N_ev_BKG_8_DC_lin;

cout<<"\nChi2/ndf = "<<Model_linear->GetChisquare()<<"/"<<Model_linear->GetNDF()<<" = "<<Model_linear->GetChisquare()/Model_linear->GetNDF()<<endl;
cout<<"\nTotal N_ev in peak region = "<<N_ev_data_8_DC_lin<<" ev/d +- "<<err_N_ev_data_8_DC_lin<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from fit = "<<N_ev_NP_8_DC_lin<<" ev/d +- "<<err_N_ev_NP_8_DC_lin<<" ev/d "<<endl;
cout<<"N_ev in background = "<<N_ev_BKG_8_DC_lin<<" ev/d +- "<<err_N_ev_BKG_8_DC_lin<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from data - bckg = "<<N_ev_data_NP_8_DC_lin<<" ev/d +- "<<err_N_ev_data_8_NP_DC_lin<<" ev/d"<<endl;

Model_linear->FixParameter(2, Model_linear->GetParameter(2)); //Fix the sigma value of the neutron peak 
Model_linear->FixParameter(1, Model_linear->GetParameter(1)); //Fix the positio. of the neutron peak  

 FCN=121.513 FROM MIGRAD    STATUS=CONVERGED     128 CALLS         129 TOTAL
                     EDM=3.74566e-07    STRATEGY= 1  ERROR MATRIX UNCERTAINTY   5.9 per cent
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  p0           1.20893e-01   5.87540e-03   4.87636e-06  -1.15140e-01
   2  p1           3.61106e+03   1.17244e+01   6.46447e-02   1.41288e-05
   3  p2           2.76051e+02     fixed    
   4  p3           2.60931e-01   1.12218e-02   1.26838e-05  -7.50643e-01
   5  p4          -4.93022e-05   2.43214e-06  -3.10499e-09  -2.95518e+03

Chi2/ndf = 121.513/51 = 2.3826

Total N_ev in peak region = 202 ev/d +- 3.17256 ev/d
N_ev in neutron peak from fit = 82.4758 ev/d +- 4.00834 ev/d 
N_ev in background = 114.071 ev/d +- 17.0766 ev/d
N_ev in neutron peak from data - bckg = 87.9294 ev/d +- 17.3688 ev/d


In [144]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hCal_DC_8inch->Draw("");
hCal_DC_8inch->GetYaxis()->SetRangeUser(1e-4, 10);
Linear_bckg->SetLineColor(kBlue);
Linear_bckg->Draw("RSAME");
Model_linear->Draw("RSAME");

TCanvas* C2 = new TCanvas("cRes_DC_8inch_lin", "cRes_DC_8inch_lin", C->GetWw(), 0.6*C->GetWh());
C2->Draw();
gPad->SetMargin(0.1,0.1,0.2,0.1);

hRes_DC_8inch_lin=Residuals(hCal_DC_8inch, Model_linear, 2800, 4700, true);
hRes_DC_8inch_lin->GetYaxis()->SetTitle("Residuals [%]");
hRes_DC_8inch_lin->GetYaxis()->SetTitleSize(2*hCal_DC_8inch->GetYaxis()->GetTitleSize());
hRes_DC_8inch_lin->GetXaxis()->SetTitleSize(2*hCal_DC_8inch->GetXaxis()->GetTitleSize());
hRes_DC_8inch_lin->GetYaxis()->SetLabelSize(2*hCal_DC_8inch->GetYaxis()->GetLabelSize());
hRes_DC_8inch_lin->GetXaxis()->SetLabelSize(2*hCal_DC_8inch->GetXaxis()->GetLabelSize());
hRes_DC_8inch_lin->Draw("");

h_10pc->SetLineColorAlpha(kOrange+1, 0.2);
h_10pc->SetMarkerColorAlpha(kOrange+1, 0.2);
h_10pc->SetFillColorAlpha(kOrange+1, 0.2);
h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10%");
leg->Draw("SAME");
leg->SetLineWidth(0);

In [145]:
Int_start = 3000;
Int_stop = 4500;

Model_linear->SetParameter(1, 3500);
if (Model_linear->GetParameter(2)==0) Model_linear->SetParameter(2, Resol_NP*3500);

TFitResultPtr r = hCal_VNS_8inch->Fit(Model_linear, "S0", "", 3000, 5100);

TMatrixD CovMat_8_lin_VNS = r->GetCovarianceMatrix();

//CovMat_DC.Print();

Double_t err_norm_8_NP_VNS_lin = sqrt(CovMat_8_lin_VNS(0,0));
Double_t norm_8_NP_VNS_lin = Model_linear->GetParameter(0);

Linear_bckg->SetParameter(0, Model_linear->GetParameter(3));
Linear_bckg->SetParameter(1, Model_linear->GetParameter(4));

Neutron_peak_Gaus->SetParameter(0, Model_linear->GetParameter(0));
Neutron_peak_Gaus->SetParameter(1, Model_linear->GetParameter(1));
Neutron_peak_Gaus->SetParameter(2, Model_linear->GetParameter(2));

Double_t N_ev_tot_8_VNS_lin = Model_linear->Integral(Int_start, Int_stop);
Double_t N_ev_NP_8_VNS_lin = Neutron_peak_Gaus->Integral(Int_start, Int_stop);
Double_t err_N_ev_NP_8_VNS_lin = (err_norm_8_NP_VNS_lin/norm_8_NP_VNS_lin)*Neutron_peak_Gaus->Integral(Int_start, Int_stop);
Double_t N_ev_BKG_8_VNS_lin = Linear_bckg->Integral(Int_start, Int_stop);
Double_t err_N_ev_BKG_8_VNS_lin = sqrt((Int_stop-Int_start)*(Int_stop-Int_start)*CovMat_8_lin_VNS(3,3)+(Int_stop-Int_start)*(Int_stop*Int_stop-Int_start*Int_start)*CovMat_8_lin_VNS(3, 4)+(Int_stop*Int_stop-Int_start*Int_start)*(Int_stop*Int_stop-Int_start*Int_start)*CovMat_8_lin_VNS(4,4)/4);

Double_t err_N_ev_data_8_VNS_lin;
Double_t N_ev_data_8_VNS_lin = hCal_VNS_8inch->IntegralAndError(hCal_VNS_8inch->FindBin(Int_start), hCal_VNS_8inch->FindBin(Int_stop), err_N_ev_data_8_VNS_lin, "width");

Double_t err_N_ev_data_8_NP_VNS_lin = sqrt(err_N_ev_data_8_VNS_lin*err_N_ev_data_8_VNS_lin + err_N_ev_BKG_8_VNS_lin*err_N_ev_BKG_8_VNS_lin);
Double_t N_ev_data_NP_8_VNS_lin = N_ev_data_8_VNS_lin-N_ev_BKG_8_VNS_lin;

cout<<"\nChi2/ndf = "<<Model_linear->GetChisquare()<<"/"<<Model_linear->GetNDF()<<" = "<<Model_linear->GetChisquare()/Model_linear->GetNDF()<<endl;
cout<<"\nTotal N_ev in peak region = "<<N_ev_data_8_VNS_lin<<" ev/d +- "<<err_N_ev_data_8_VNS_lin<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from fit = "<<N_ev_NP_8_VNS_lin<<" ev/d +- "<<err_N_ev_NP_8_VNS_lin<<" ev/d "<<endl;
cout<<"N_ev in background = "<<N_ev_BKG_8_VNS_lin<<" ev/d +- "<<err_N_ev_BKG_8_VNS_lin<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from data - bckg = "<<N_ev_data_NP_8_VNS_lin<<" ev/d +- "<<err_N_ev_data_8_NP_VNS_lin<<" ev/d"<<endl;

Model_linear->FixParameter(2, Model_linear->GetParameter(2)); //Fix the sigma value of the neutron peak  

 FCN=111.895 FROM MIGRAD    STATUS=CONVERGED     189 CALLS         190 TOTAL
                     EDM=2.57351e-09    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  p0           1.12782e-02   2.50996e-03   2.09870e-05  -7.59951e-03
   2  p1           3.50000e+03     fixed    
   3  p2           2.76051e+02     fixed    
   4  p3           1.07448e-01   6.14695e-03   2.09553e-06  -1.13370e-01
   5  p4          -2.06653e-05   1.31330e-06   4.65081e-10  -5.66369e+02

Chi2/ndf = 111.895/47 = 2.38074

Total N_ev in peak region = 57.6136 ev/d +- 1.1077 ev/d
N_ev in neutron peak from fit = 7.52933 ev/d +- 1.67567 ev/d 
N_ev in background = 44.9294 ev/d +- 9.35255 ev/d
N_ev in neutron peak from data - bckg = 12.6842 ev/d +- 9.41792 ev/d


In [146]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hCal_VNS_8inch->Draw("");
hCal_VNS_8inch->GetYaxis()->SetRangeUser(1e-4, 10);
Linear_bckg->SetLineColor(kBlue);
Linear_bckg->Draw("RSAME");
Model_linear->Draw("RSAME");

TCanvas* C2 = new TCanvas("cRes_VNS_8inch_lin", "cRes_VNS_8inch_lin", C->GetWw(), 0.6*C->GetWh());
C2->Draw();
gPad->SetMargin(0.1,0.1,0.2,0.1);

hRes_VNS_8inch_lin=Residuals(hCal_VNS_8inch, Model_linear, 3000, 4700, true);
hRes_VNS_8inch_lin->GetYaxis()->SetTitle("Residuals [%]");
hRes_VNS_8inch_lin->GetYaxis()->SetTitleSize(2*hCal_VNS_8inch->GetYaxis()->GetTitleSize());
hRes_VNS_8inch_lin->GetXaxis()->SetTitleSize(2*hCal_VNS_8inch->GetXaxis()->GetTitleSize());
hRes_VNS_8inch_lin->GetYaxis()->SetLabelSize(2*hCal_VNS_8inch->GetYaxis()->GetLabelSize());
hRes_VNS_8inch_lin->GetXaxis()->SetLabelSize(2*hCal_VNS_8inch->GetXaxis()->GetLabelSize());
hRes_VNS_8inch_lin->Draw("");

h_10pc->SetLineColorAlpha(kOrange+1, 0.2);
h_10pc->SetMarkerColorAlpha(kOrange+1, 0.2);
h_10pc->SetFillColorAlpha(kOrange+1, 0.2);
h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10%");
leg->Draw("SAME");
leg->SetLineWidth(0);

# Investigate the high energy background discrepancy at surface

It has been identified that at high energy, at surface, the background is not well reproduced by the model, underestimateing the numbe of high energy events. <br>
Is it a problem of MV cut? A simulation problem? Other contributions? (protons)

## Fit in Cryolab

Background model

In [147]:
TF1* Muon_peak_9inch45deg_noMV = new TF1("Muon_peak_9inch45deg_noMV", "landau", 800, 1800); //Landau in muon peak region
Muon_peak_9inch45deg_noMV->SetParNames("Amplitude_mu []", "MPV [keVee]", "[Sigma [keVee]]");
Muon_peak_9inch45deg_noMV->SetParameters(1,1100,100);
h_SimuMuons_9inch45deg_noMV->Fit("Muon_peak_9inch45deg_noMV", "R");

Muon_peak_9inch45deg_noMV->FixParameter(0,Muon_peak_9inch45deg_noMV->GetParameter(0));
Muon_peak_9inch45deg_noMV->FixParameter(1,Muon_peak_9inch45deg_noMV->GetParameter(1));
Muon_peak_9inch45deg_noMV->FixParameter(2,Muon_peak_9inch45deg_noMV->GetParameter(2));

TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_9inch45deg_noMV->Draw("SAME");

 FCN=24.8081 FROM MIGRAD    STATUS=CONVERGED     126 CALLS         127 TOTAL
                     EDM=1.46856e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Amplitude_mu []   4.08745e+00   1.93103e-02   3.16266e-05   9.19461e-03
   2  MPV [keVee]   1.10600e+03   2.17831e+00   5.21125e-03  -4.26895e-05
   3  [Sigma [keVee]]   2.17524e+02   2.05282e+00   4.70447e-06   4.88240e-02


In [148]:
TF1* Muon_plateau_9inch45deg_noMV = new TF1("Muon_plateau_9inch45deg_noMV", "pol4", 100, 900); 
Muon_plateau_9inch45deg_noMV->SetParNames("a", "b", "c", "d", "e");
h_SimuMuons_9inch45deg_noMV->Fit("Muon_plateau_9inch45deg_noMV", "R");

Muon_plateau_9inch45deg_noMV->FixParameter(0,Muon_plateau_9inch45deg_noMV->GetParameter(0));
Muon_plateau_9inch45deg_noMV->FixParameter(1,Muon_plateau_9inch45deg_noMV->GetParameter(1));
Muon_plateau_9inch45deg_noMV->FixParameter(2,Muon_plateau_9inch45deg_noMV->GetParameter(2));
Muon_plateau_9inch45deg_noMV->FixParameter(3,Muon_plateau_9inch45deg_noMV->GetParameter(3));
Muon_plateau_9inch45deg_noMV->FixParameter(4,Muon_plateau_9inch45deg_noMV->GetParameter(4));

TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_9inch45deg_noMV->Draw("SAME");


****************************************
Minimizer is Linear / Migrad
Chi2                      =      140.428
NDf                       =           14
a                         =      1.77175   +/-   0.0364696   
b                         =   -0.0101788   +/-   0.000379209 
c                         =  2.65429e-05   +/-   1.32357e-06 
d                         =  -3.1061e-08   +/-   1.87478e-09 
e                         =  1.40531e-11   +/-   9.25324e-13 


In [149]:
TF1* Muon_queue_9inch45deg_noMV_start = new TF1("Muon_queue_9inch45deg_noMV_start", "expo(0)", 1800, 3000); 
Muon_queue_9inch45deg_noMV_start->SetParameter(0, -10);
Muon_queue_9inch45deg_noMV_start->SetParameter(1, -0.003);
h_SimuMuons_9inch45deg_noMV->Fit("Muon_queue_9inch45deg_noMV_start", "S0R");

TF1* Muon_queue_9inch45deg_noMV_end = new TF1("Muon_queue_9inch45deg_noMV_end", "expo(0)", 4500, 5500); 
Muon_queue_9inch45deg_noMV_end->SetParameter(0, -10);
Muon_queue_9inch45deg_noMV_end->SetParameter(1, -0.003);
h_SimuMuons_9inch45deg_noMV->Fit("Muon_queue_9inch45deg_noMV_end", "S0R");

TF1* Muon_queue_secn_9inch45deg_noMV = new TF1("Muon_queue_secn_9inch45deg_noMV", "expo(0)+gaus(2)+expo(5)", 1800, 5500); 
//Muon_queue_9inch->SetParNames("Norm", "slope", "Norm_NP", "mean_NP", "sigma_NP");
Muon_queue_secn_9inch45deg_noMV->SetParameter(0, Muon_queue_9inch45deg_noMV_start->GetParameter(0));
Muon_queue_secn_9inch45deg_noMV->SetParameter(1, Muon_queue_9inch45deg_noMV_start->GetParameter(1));
Muon_queue_secn_9inch45deg_noMV->SetParameter(2, 0.011);
Muon_queue_secn_9inch45deg_noMV->SetParameter(3, 3500);
Muon_queue_secn_9inch45deg_noMV->SetParameter(4, 300);
Muon_queue_secn_9inch45deg_noMV->SetParameter(5, Muon_queue_9inch45deg_noMV_end->GetParameter(0));
Muon_queue_secn_9inch45deg_noMV->SetParameter(6, Muon_queue_9inch45deg_noMV_end->GetParameter(1));

Muon_queue_secn_9inch45deg_noMV->SetParLimits(3, 3500, 3800);
Muon_queue_secn_9inch45deg_noMV->SetParLimits(2, 0., 1000);
Muon_queue_secn_9inch45deg_noMV->SetParLimits(4, 100, 600);
h_SimuMuons_9inch45deg_noMV->Fit("Muon_queue_secn_9inch45deg_noMV", "S0R");

Muon_queue_secn_9inch45deg_noMV->FixParameter(0, Muon_queue_secn_9inch45deg_noMV->GetParameter(0));
Muon_queue_secn_9inch45deg_noMV->FixParameter(1, Muon_queue_secn_9inch45deg_noMV->GetParameter(1));
Muon_queue_secn_9inch45deg_noMV->FixParameter(2, Muon_queue_secn_9inch45deg_noMV->GetParameter(2));
Muon_queue_secn_9inch45deg_noMV->FixParameter(3, Muon_queue_secn_9inch45deg_noMV->GetParameter(3));
Muon_queue_secn_9inch45deg_noMV->FixParameter(4, Muon_queue_secn_9inch45deg_noMV->GetParameter(4));
Muon_queue_secn_9inch45deg_noMV->FixParameter(5, Muon_queue_secn_9inch45deg_noMV->GetParameter(5));
Muon_queue_secn_9inch45deg_noMV->FixParameter(6, Muon_queue_secn_9inch45deg_noMV->GetParameter(6));

 FCN=48.2089 FROM MIGRAD    STATUS=CONVERGED      55 CALLS          56 TOTAL
                     EDM=1.12297e-14    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant     7.70368e-01   3.85043e-02   1.84770e-05   2.34339e-05
   2  Slope       -1.14294e-03   1.68726e-05   8.09659e-09   4.81793e-02
 FCN=13.6916 FROM MIGRAD    STATUS=CONVERGED      43 CALLS          44 TOTAL
                     EDM=1.88384e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant    -4.36835e-01   3.43189e-01   3.35910e-05  -3.41271e-02
   2  Slope       -7.28850e-04   6.95190e-05   6.80286e-09  -1.67669e+02
 FCN=93.4798 FROM MIGRAD    STATUS=CONVERGED    1653 CALLS        1654 TOTAL
                     EDM=7.45

In [150]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_9inch45deg_noMV->Draw("");
Muon_queue_secn_9inch45deg_noMV->Draw("SAME");
Muon_queue_9inch45deg_noMV_end->SetLineColor(kBlue);
Muon_queue_9inch45deg_noMV_end->Draw("SAME");
Muon_queue_9inch45deg_noMV_start->SetLineColor(kBlue);
Muon_queue_9inch45deg_noMV_start->Draw("SAME");

In [151]:
Double_t Muons_9inch45deg_noMV(Double_t* x, Double_t *par){
    Double_t par_cdf[2]= {par[3], par[4]};
    Double_t par_cdf2[2]= {par[5], par[6]};
    return (1-cdf(x, par_cdf))*par[0]*Muon_plateau_9inch45deg_noMV->Eval(x[0])+cdf(x, par_cdf)*(1-cdf(x, par_cdf2))*par[1]*Muon_peak_9inch45deg_noMV->Eval(x[0])+cdf(x, par_cdf2)*par[2]*Muon_queue_secn_9inch45deg_noMV->Eval(x[0]);
}

In [152]:
TF1* Muon_shape_9inch45deg_noMV = new TF1("Muon_shape_9inch45deg_noMV", Muons_9inch45deg_noMV, 150, 5500, 7);
Muon_shape_9inch45deg_noMV->SetParNames("Norm_plateau", "Norm_muonpeak", "Norm_muonqueue", "pos cdf", "sigma cdf", "pos cdf2", "sigma cdf2");

Muon_shape_9inch45deg_noMV->SetParameter(0, 1);
Muon_shape_9inch45deg_noMV->SetParameter(1, 1);
Muon_shape_9inch45deg_noMV->SetParameter(2, 1);

Muon_shape_9inch45deg_noMV->SetParameter(3, 850);
Muon_shape_9inch45deg_noMV->SetParameter(4, 400);
Muon_shape_9inch45deg_noMV->SetParLimits(4, 0, 500);
Muon_shape_9inch45deg_noMV->SetParLimits(3, 800, 1400);
Muon_shape_9inch45deg_noMV->SetParameter(5, 2400);
Muon_shape_9inch45deg_noMV->SetParLimits(5, 2000, 6000);
Muon_shape_9inch45deg_noMV->SetParameter(6, 400);
Muon_shape_9inch45deg_noMV->SetParLimits(6, 0, 500);
h_SimuMuons_9inch45deg_noMV->Fit("Muon_shape_9inch45deg_noMV", "R0");

TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
h_SimuMuons_9inch45deg_noMV->Draw();
Muon_shape_9inch45deg_noMV->Draw("SAME");

 FCN=215.486 FROM MIGRAD    STATUS=CONVERGED     859 CALLS         860 TOTAL
                     EDM=3.43514e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_plateau   9.82034e-01   7.10647e-03   3.15610e-05  -5.70233e-02
   2  Norm_muonpeak   9.92614e-01   4.12704e-03   2.38419e-05   2.15419e-01
   3  Norm_muonqueue   1.01304e+00   5.76238e-03   3.89173e-05  -6.40229e-03
   4  pos cdf      8.02634e+02   4.45087e+02   5.00000e-01   1.51091e-06
   5  sigma cdf    6.32049e-01   3.46174e+02   5.48255e-03   5.18403e-12
   6  pos cdf2     2.00000e+03   2.26142e+01   1.08757e-03** at limit **
   7  sigma cdf2   4.95743e+02   4.38941e+01   2.57360e-03   4.59609e-04


In [153]:
Muon_shape_9inch45deg_noMV->FixParameter(0, Muon_shape_9inch45deg_noMV->GetParameter(0));
Muon_shape_9inch45deg_noMV->FixParameter(1, Muon_shape_9inch45deg_noMV->GetParameter(1));
Muon_shape_9inch45deg_noMV->FixParameter(2, Muon_shape_9inch45deg_noMV->GetParameter(2));
Muon_shape_9inch45deg_noMV->FixParameter(3, Muon_shape_9inch45deg_noMV->GetParameter(3));
Muon_shape_9inch45deg_noMV->FixParameter(4, Muon_shape_9inch45deg_noMV->GetParameter(4));
Muon_shape_9inch45deg_noMV->FixParameter(5, Muon_shape_9inch45deg_noMV->GetParameter(5));
Muon_shape_9inch45deg_noMV->FixParameter(6, Muon_shape_9inch45deg_noMV->GetParameter(6));

In [154]:
Double_t MuonsplusGammas_9inch_noMV(Double_t* x, Double_t *par){
    return par[0]*Muon_shape_9inch45deg_noMV->Eval(x[0])+par[1]*Gamma_shape_9inch->Eval(x[0]);
}

TF1* Sum_background_9inch_noMV = new TF1("Sum_background_9inch_noMV", MuonsplusGammas_9inch_noMV, 400, 6000, 2);
Sum_background_9inch_noMV->SetParNames("Norm_muons", "Norm_gammas");

In [155]:
Double_t Muons_9inch_noMV(Double_t* x, Double_t *par){
    return par[0]*Muon_shape_9inch45deg_noMV->Eval(x[0]);
}

TF1* Muon_background_9inch_noMV = new TF1("Muon_background_9inch_noMV", Muons_9inch_noMV, 50, 6000, 1);
Muon_background_9inch_noMV->SetParNames("Norm_muons");

In [156]:
Double_t SignalPlusBackground_9inch_noMV(Double_t* x, Double_t *par){
    Neutron_shape->SetParameter(1, par[3]);
    Neutron_shape->SetParameter(2, par[4]);
    return par[0]*Muon_shape_9inch45deg_noMV->Eval(x[0])+par[1]*Gamma_shape_9inch->Eval(x[0])+par[2]*Neutron_shape->Eval(x[0]);
}

TF1* SignalandBackground_9inch_noMV = new TF1("SignalandBackground_9inch_noMV", SignalPlusBackground_9inch_noMV, 100, 5000, 5);
SignalandBackground_9inch_noMV->SetParNames("Norm_muons", "Norm_gammas", "Norm_Neutr", "Mean_gauss", "Sigma_gauss");

In [157]:
SignalandBackground_9inch_noMV->SetParameter(3, 3500);
SignalandBackground_9inch_noMV->SetParLimits(3, 3000, 4000);
SignalandBackground_9inch_noMV->SetParLimits(4, 100, 500);
SignalandBackground_9inch_noMV->SetParameter(2, 1);
if (SignalandBackground_9inch_noMV->GetParameter(4)==0) SignalandBackground_9inch_noMV->SetParameter(4, Resol_NP*3500);

TFitResultPtr r = hCal_CryoLab_9inch->Fit(SignalandBackground_9inch_noMV, "S0", "", 700, 6000);

TMatrixD CovMat_CL = r->GetCovarianceMatrix();

Double_t err_norm_NP_CL = sqrt(CovMat_CL(2,2));
Double_t norm_NP_CL = SignalandBackground_9inch_noMV->GetParameter(2);

Double_t err_norm_Bkg_CL = sqrt(CovMat_CL(0,0)+CovMat_CL(1,1)+2*CovMat_CL(0,1));
Double_t norm_Bckg_CL = SignalandBackground_9inch_noMV->GetParameter(0)+SignalandBackground_9inch_noMV->GetParameter(1);

Double_t Norm_mu_9_CL = SignalandBackground_9inch_noMV->GetParameter(0);
Double_t err_Norm_mu_9_CL = SignalandBackground_9inch_noMV->GetParError(0);

Sum_background_9inch_noMV->SetParameter(0, SignalandBackground_9inch_noMV->GetParameter(0));
Sum_background_9inch_noMV->SetParameter(1, SignalandBackground_9inch_noMV->GetParameter(1));

Muon_background_9inch_noMV->SetParameter(0, SignalandBackground_9inch_noMV->GetParameter(0));
Gamma_background_9inch->SetParameter(0, SignalandBackground_9inch_noMV->GetParameter(1));

Neutron_signal_9inch->SetParameter(0, SignalandBackground_9inch_noMV->GetParameter(2));
Neutron_signal_9inch->SetParameter(1, SignalandBackground_9inch_noMV->GetParameter(3));
Neutron_signal_9inch->SetParameter(2, SignalandBackground_9inch_noMV->GetParameter(4));

Double_t N_ev_tot_CL = SignalandBackground_9inch->Integral(Emin, Emax);
Double_t N_ev_NP_CL = Neutron_signal_9inch->Integral(Emin, Emax);
Double_t err_N_ev_NP_CL = (err_norm_NP_CL/norm_NP_CL)*Neutron_signal_9inch->Integral(Emin, Emax);
Double_t N_ev_BKG_CL = Sum_background_9inch->Integral(Emin, Emax);
Double_t err_N_ev_BKG_CL = (err_norm_Bkg_CL/norm_Bckg_CL)*Sum_background_9inch->Integral(Emin, Emax);

Double_t err_N_ev_data_CL;
Double_t N_ev_data_CL = hCal_CryoLab_9inch->IntegralAndError(hCal_CryoLab_9inch->FindBin(Emin), hCal_DC_9inch->FindBin(Emax), err_N_ev_data_DC, "width");

Double_t err_N_ev_data_NP_CL = sqrt(err_N_ev_data_CL*err_N_ev_data_CL + err_N_ev_BKG_CL*err_N_ev_BKG_CL);
Double_t N_ev_data_NP_CL = N_ev_data_CL-N_ev_BKG_CL;

cout<<"\nChi2/ndf = "<<SignalandBackground_9inch->GetChisquare()<<"/"<<SignalandBackground_9inch->GetNDF()<<" = "<<SignalandBackground_9inch->GetChisquare()/SignalandBackground_9inch->GetNDF()<<endl;
cout<<"\nTotal N_ev in peak region = "<<N_ev_data_CL<<" ev/d +- "<<err_N_ev_data_CL<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from fit = "<<N_ev_NP_CL<<" ev/d +- "<<err_N_ev_NP_CL<<" ev/d (error from normalization error only!)"<<endl;
cout<<"N_ev in background = "<<N_ev_BKG_CL<<" ev/d +- "<<err_N_ev_BKG_CL<<" ev/d"<<endl;
cout<<"N_ev in neutron peak from data - bckg = "<<N_ev_data_NP_CL<<" ev/d +- "<<err_N_ev_data_NP_CL<<" ev/d"<<endl;

SignalandBackground_9inch->FixParameter(4, SignalandBackground_9inch->GetParameter(4)); //Fix the sigma value of the neutron peak

 FCN=154.156 FROM MIGRAD    STATUS=CONVERGED     154 CALLS         155 TOTAL
                     EDM=8.99358e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   1.60337e+00   3.93664e-02   1.64999e-04  -1.23647e-02
   2  Norm_gammas   3.91483e-01   4.83842e-02   2.09235e-04   1.54095e-03
   3  Norm_Neutr   4.18693e-01   3.11257e-02   1.54545e-04  -1.55964e-02
   4  Mean_gauss   3.46654e+03   2.03318e+01   2.43793e-04   2.93555e-02
   5  Sigma_gauss   2.69949e+02   1.77752e+01   4.31748e-04  -1.45640e-04

Chi2/ndf = 168.453/104 = 1.61974

Total N_ev in peak region = 254.333 ev/d +- 0 ev/d
N_ev in neutron peak from fit = 142.461 ev/d +- 10.5906 ev/d (error from normalization error only!)
N_ev in background = 47.2175 ev/d +- 0.824051 ev/d
N_ev in neutron peak from data - bckg = 207.116 ev/d +- 0.824051 ev/d


In [158]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();

hCal_CryoLab_9inch->Draw("");
SignalandBackground_9inch_noMV->SetLineColor(kBlack);
hCal_CryoLab_9inch->GetYaxis()->SetRangeUser(1e-4, 10);
Sum_background_9inch_noMV->SetLineColor(kBlue);
Sum_background_9inch_noMV->Draw("RSAME");
Muon_background_9inch_noMV->SetLineColor(kGreen);
Gamma_background_9inch->SetLineColor(kRed);
Muon_background_9inch_noMV->Draw("RSAME");
Gamma_background_9inch->Draw("RSAME");
Sum_background_9inch_noMV->Draw("RSAME");
SignalandBackground_9inch_noMV->Draw("RSAME");
Neutron_signal_9inch->SetLineColor(kMagenta);
Neutron_signal_9inch->Draw("RSAME");

TLegend* leg0 = new TLegend(0.6, 0.7, 0.89, 0.89);
leg0->AddEntry(Sum_background_9inch_noMV, "Background");
leg0->AddEntry(SignalandBackground_9inch_noMV, "Signal and Bckg");
leg0->AddEntry(Neutron_signal_9inch, "Neutron Signal");
leg0->AddEntry(Muon_background_9inch_noMV, "Muon Bckg");
leg0->AddEntry(Gamma_background_9inch, "Gamma Bckg");
leg0->Draw("SAME");
leg0->SetLineWidth(0);


TCanvas* C2 = new TCanvas("cRes_CL_8inch", "cRes_CL_8inch", 1.175*C->GetWw(), 0.6*C->GetWh());
C2->Draw();
TPad *p1 = new TPad("p1","p1",0.,0.02,0.795,1.);
p1->Draw();
p1->cd();
p1->SetRightMargin(0.03);
p1->SetBottomMargin(0.2);

histosRes_CL_9inch = Residuals_vec(hCal_CryoLab_9inch, SignalandBackground_9inch_noMV, 500, 6000, true);
hRes_CL_9inch=histosRes_CL_9inch[0];
hRes_CL_9inch->GetYaxis()->SetTitle("Residuals [%]");
hRes_CL_9inch->GetYaxis()->SetTitleSize(1.9*hCal_CryoLab_9inch->GetYaxis()->GetTitleSize());
hRes_CL_9inch->GetXaxis()->SetTitleSize(1.9*hCal_CryoLab_9inch->GetXaxis()->GetTitleSize());
hRes_CL_9inch->GetYaxis()->SetLabelSize(1.9*hCal_CryoLab_9inch->GetYaxis()->GetLabelSize());
hRes_CL_9inch->GetXaxis()->SetLabelSize(1.9*hCal_CryoLab_9inch->GetXaxis()->GetLabelSize());
hRes_CL_9inch->Draw("");

h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10%");
leg->Draw("SAME");
leg->SetLineWidth(0);


C2->cd();
TPad *p2 = new TPad("p2","p2",0.795,0.02,0.9,1.);
p2->Draw();
p2->cd();
p2->SetLeftMargin(0.15);
p2->SetBottomMargin(0.2);

hRedRes_CL_9inch=histosRes_CL_9inch[1];
hRedRes_CL_9inch->Draw("");
hRedRes_CL_9inch->GetXaxis()->SetTitle("Residuals [#sigma]");
hRedRes_CL_9inch->GetYaxis()->SetTitleSize(3.*hCal_CryoLab_9inch->GetYaxis()->GetTitleSize());
hRedRes_CL_9inch->GetXaxis()->SetTitleSize(2.7*hCal_CryoLab_9inch->GetXaxis()->GetTitleSize());
hRedRes_CL_9inch->GetXaxis()->SetTitleOffset(0.7);
hRedRes_CL_9inch->GetYaxis()->SetLabelSize(3.*hCal_CryoLab_9inch->GetYaxis()->GetLabelSize());
hRedRes_CL_9inch->GetXaxis()->SetLabelSize(2.7*hCal_CryoLab_9inch->GetXaxis()->GetLabelSize());
hRedRes_CL_9inch->GetXaxis()->SetNdivisions(5);

In [159]:
SignalandBackground_9inch->SetParameter(3, 3500);
SignalandBackground_9inch->SetParLimits(3, 3000, 4000);
SignalandBackground_9inch->SetParLimits(4, 100, 500);
SignalandBackground_9inch->SetParameter(2, 1);
if (SignalandBackground_9inch->GetParameter(4)==0) SignalandBackground_9inch->SetParameter(4, Resol_NP*3500);

TFitResultPtr r = hCal_CryoLab_9inch->Fit(SignalandBackground_9inch, "S0", "", 100, 6000);

TMatrixD CovMat_CL = r->GetCovarianceMatrix();


Double_t err_norm_NP_CL = sqrt(CovMat_CL(2,2));
Double_t norm_NP_CL = SignalandBackground_9inch->GetParameter(2);

Double_t err_norm_Bkg_CL = sqrt(CovMat_CL(0,0)+CovMat_CL(1,1)+2*CovMat_CL(0,1));
Double_t norm_Bckg_CL = SignalandBackground_9inch->GetParameter(0)+SignalandBackground_9inch->GetParameter(1);

Double_t Norm_mu_9_CL = SignalandBackground_9inch->GetParameter(0);
Double_t err_Norm_mu_9_CL = SignalandBackground_9inch->GetParError(0);

Sum_background_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(0));
Sum_background_9inch->SetParameter(1, SignalandBackground_9inch->GetParameter(1));

Muon_background_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(0));
Gamma_background_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(1));

Neutron_signal_9inch->SetParameter(0, SignalandBackground_9inch->GetParameter(2));
Neutron_signal_9inch->SetParameter(1, SignalandBackground_9inch->GetParameter(3));
Neutron_signal_9inch->SetParameter(2, SignalandBackground_9inch->GetParameter(4));

 FCN=221.546 FROM MIGRAD    STATUS=CONVERGED     166 CALLS         167 TOTAL
                     EDM=6.40628e-10    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Norm_muons   2.35621e-01   5.34869e-03   3.35592e-05   3.46902e-03
   2  Norm_gammas   8.29476e-01   1.57460e-02   1.02760e-04   1.62525e-03
   3  Norm_Neutr   4.23981e-01   2.93620e-02   1.56063e-04  -1.06810e-03
   4  Mean_gauss   3.46277e+03   2.11067e+01   2.92097e-04  -2.41607e-04
   5  Sigma_gauss   3.43299e+02   2.26571e+01   5.83641e-04  -2.55933e-04


In [160]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();

hCal_CryoLab_9inch->Draw("");
SignalandBackground_9inch->SetLineColor(kBlack);
hCal_CryoLab_9inch->GetYaxis()->SetRangeUser(1e-4, 10);
Sum_background_9inch->SetLineColor(kBlue);
Sum_background_9inch->Draw("RSAME");
Muon_background_9inch->SetLineColor(kGreen);
Gamma_background_9inch->SetLineColor(kRed);
Muon_background_9inch->Draw("RSAME");
Gamma_background_9inch->Draw("RSAME");
Sum_background_9inch->Draw("RSAME");
SignalandBackground_9inch->Draw("RSAME");
Neutron_signal_9inch->SetLineColor(kMagenta);
Neutron_signal_9inch->Draw("RSAME");

TLegend* leg0 = new TLegend(0.6, 0.7, 0.89, 0.89);
leg0->AddEntry(Sum_background_9inch, "Background");
leg0->AddEntry(SignalandBackground_9inch, "Signal and Bckg");
leg0->AddEntry(Neutron_signal_9inch, "Neutron Signal");
leg0->AddEntry(Muon_background_9inch, "Muon Bckg");
leg0->AddEntry(Gamma_background_9inch, "Gamma Bckg");
leg0->Draw("SAME");
leg0->SetLineWidth(0);

TCanvas* C2 = new TCanvas("cRes_CL_9inch", "cRes_CL_9inch", 1.175*C->GetWw(), 0.6*C->GetWh());
C2->Draw();
TPad *p1 = new TPad("p1","p1",0.,0.02,0.795,1.);
p1->Draw();
p1->cd();
p1->SetRightMargin(0.03);
p1->SetBottomMargin(0.2);

histosRes_CryoLab_9inch = Residuals_vec(hCal_CryoLab_9inch, SignalandBackground_9inch, 100, 6000, true);
hRes_CryoLab_9inch=histosRes_CryoLab_9inch[0];
hRes_CryoLab_9inch->GetYaxis()->SetTitle("Residuals [%]");
hRes_CryoLab_9inch->GetYaxis()->SetTitleSize(1.9*hCal_CryoLab_9inch->GetYaxis()->GetTitleSize());
hRes_CryoLab_9inch->GetXaxis()->SetTitleSize(1.9*hCal_CryoLab_9inch->GetXaxis()->GetTitleSize());
hRes_CryoLab_9inch->GetYaxis()->SetLabelSize(1.9*hCal_CryoLab_9inch->GetYaxis()->GetLabelSize());
hRes_CryoLab_9inch->GetXaxis()->SetLabelSize(1.9*hCal_CryoLab_9inch->GetXaxis()->GetLabelSize());
hRes_CryoLab_9inch->Draw("");

h_10pc->Draw("E3SAME");

TLegend* leg = new TLegend(0.15, 0.3, 0.30, 0.4);
leg->AddEntry(h_10pc, "10%");
leg->Draw("SAME");
leg->SetLineWidth(0);

C2->cd();
TPad *p2 = new TPad("p2","p2",0.795,0.02,1.,1.);
p2->Draw();
p2->cd();
p2->SetLeftMargin(0.15);
p2->SetBottomMargin(0.2);

hRedRes_CryoLab_9inch=histosRes_CryoLab_9inch[1];
hRedRes_CryoLab_9inch->Draw("");
hRedRes_CryoLab_9inch->GetXaxis()->SetTitle("Residuals [#sigma]");
hRedRes_CryoLab_9inch->GetYaxis()->SetTitleSize(3.*hCal_CryoLab_9inch->GetYaxis()->GetTitleSize());
hRedRes_CryoLab_9inch->GetXaxis()->SetTitleSize(2.7*hCal_CryoLab_9inch->GetXaxis()->GetTitleSize());
hRedRes_CryoLab_9inch->GetXaxis()->SetTitleOffset(0.7);
hRedRes_CryoLab_9inch->GetYaxis()->SetLabelSize(3.*hCal_CryoLab_9inch->GetYaxis()->GetLabelSize());
hRedRes_CryoLab_9inch->GetXaxis()->SetLabelSize(2.7*hCal_CryoLab_9inch->GetXaxis()->GetLabelSize());
hRedRes_CryoLab_9inch->GetXaxis()->SetNdivisions(5);

Warning in <TFile::Append>: Replacing existing TH1: Reduced_res_ (Potential memory leak).


## Saclay

In [161]:
TH1D* h_Saclay_8inch = Put_data_in_histo("Measures@Saclay/2022-10-25_BS-A-06_RT_597901.88_LV_597845.67.dat", 597845., "8inch at Saclay");
h_Saclay_8inch->Rebin(4);
h_Saclay_8inch->Scale(1/4.);


*******************************************************
Measures@Saclay/2022-10-25_BS-A-06_RT_597901.88_LV_597845.67.dat


In [162]:
//Saclay
TH1D* hCal_Saclay_8inch = Calibrate_histo(h_Saclay_8inch, Cal_factor_8inch, Form("%s_keVee", h_Saclay_8inch->GetTitle()));

In [163]:
TH1D* h_CryoLab_8inch = Put_data_in_histo("Measures@TUM/02-18_BkgSpektrum_CryoLab__BS-A-06_44h.dat", 44*3600, "8inch at Cryolab atm neutrons");
h_CryoLab_8inch->Rebin(4);
h_CryoLab_8inch->Scale(1/4.);


*******************************************************
Measures@TUM/02-18_BkgSpektrum_CryoLab__BS-A-06_44h.dat


In [164]:
//Saclay
TH1D* hCal_CryoLab_8inch = Calibrate_histo(h_CryoLab_8inch, Cal_factor_8inch, Form("%s_keVee", h_CryoLab_8inch->GetTitle()));

In [165]:
TCanvas* C = new TCanvas();
C->Draw();
C->SetLogy();
hCal_CryoLab_8inch->SetLineColor(kBlack);
hCal_CryoLab_8inch->Draw("SAME");
//hCal_Saclay_8inch->SetLineColor(kGreen);
//hCal_Saclay_8inch->Draw("SAME");
//hCal_DC_8inch->SetLineColor(kRed);
//hCal_DC_8inch->Draw("SAME");
hCal_VNS_8inch->SetLineColor(kBlue);
hCal_VNS_8inch->Draw("SAME");

hCal_CryoLab_8inch->SetTitle("");
TLegend* leg0 = new TLegend(0.6, 0.7, 0.89, 0.89);
leg0->AddEntry(hCal_CryoLab_8inch, "Cryolab (no MV)");
//leg0->AddEntry(hCal_Saclay_8inch, "Saclay (no MV)");
//leg0->AddEntry(hCal_DC_8inch, "DCHut (with MV)");
leg0->AddEntry(hCal_VNS_8inch, "VNS (with MV)");
leg0->Draw("SAME");
leg0->SetLineWidth(0);